<a href="https://colab.research.google.com/github/johnzelson/nonprofits-colab/blob/main/S2_Get_City_Demogs.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Overview

S2 Get Demographics for City

Adds "Nice to have" demographics about the city and county where the nonprofit is located.

In Step 1, a dataframe of 1522 cities was created from all the unique city names in the IRS BMF of active nonprofits

Adding some demographic info at city (and maybe county level).  This gives some additional context for nonprofits that could be useful in an analysis.

As indicated in relevant places in code, trying match postal address city in BMF to census codes is not satisfactory.  Tried a variety of datasets from USGS, Google Data commons, and different cuts of Census to unambigously resolve.  One could geocode all nonprofits (at 10k per day at Census), but a practical  solution is to just geocode the addresses of orgs where match was unsuccessful.


# Tech Notes

|   In         | Description                   |
| ------------ |-------------------------------|
| bmf_cities_precensus_df   | unique cities with rankings   |

|   Out         | Description                   |
| ------------ |-------------------------------|
| bmf_cities_p_df   | city list with demographics   |  

Of the 1522 cities, 429 were not matched to demographic info.

Note:  Looking up demographics by city name is not satisfactory.  Some experiments with other datasets left in below.  Eg. Using USGS list of populated places, Google Data Commons,  and various queries of US Census.






# Setup


In [ ]:
from google.colab import drive
drive.mount('/content/drive', force_remount=True)


Mounted at /content/drive


In [ ]:
from google.colab import userdata


In [ ]:
#TODO: create a configuration section -- not implemented

# base folder for retrieving raw data
data_dir = '/content/drive/My Drive/irs_data/'

# folder for writing processed data
proc_dir = '/content/drive/My Drive/IRS_processed/'


In [ ]:
import pandas as pd
pd.set_option('display.max_columns', 100);
pd.set_option('display.max_rows', 50);

# note:  in colab, if max rows has to be greater than the rows returned
# or display will revert to head and tail defaults


In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pprint
import csv
import math
import requests
from google.colab import userdata

# Load processed nonprofits and city dataframes

Goal is to match city name to census, mostly for population.


In [ ]:
# in case loading processed ny data
# at this step, has all NY nonprofits with uszipcode library into added

dtype = {"CLASSIFICATION": str,
         "EIN" : str,
         "ACTIVITY" : str,
         "AFFILIATION" : str,
         "ORGANIZATION" : str,
         "FOUNDATION" : str,
         "NTEE_CD" : str,
         "RULING" : str,
         "ZIP" : str,
         "TAX_PERIOD" : str,
         "GROUP" : str,
         "cb_BASENAME" : int,
         "cb_BLKGRP" : int,
         "cb_BLOCK": str,
         "cb_GEOID" : str,
         "ZipCd" : str,
         "zipcode" : str,
         #"population" : int,
         #"housing_units" : int,
         # TypeError: Cannot cast array data from dtype('float64') to dtype('int64') according to the rule 'safe'

         #"occupied_housing_units" : int,
         #"median_home_value" : int,
         #"median_household_income": int
         }

df = pd.read_csv('/content/drive/My Drive/IRS_processed/np_ny_p_df.csv', dtype=dtype)
display(df)

#https://tools.geofabrik.de/calc/#type=geofabrik_standard&bbox=-76.32906,42.444656,-75.919193,42.727212&tab=1&proj=EPSG:4326&places=4

bbox=-76.32906,42.444656,-75.919193,42.727212

&tab=1&proj=EPSG:4326&places=4

flds = ['major_city', 'bounds_west',  'bounds_south',  'bounds_east',  'bounds_north']
df[flds]

-74.012702, 	40.619712, 	-73.981181, 	40.647101



major_city  bounds_west  bounds_south  bounds_east  bounds_north
0               Brooklyn   -74.012702     40.619712   -73.981181     40.647101
1           Orchard Park   -78.809896     42.671722   -78.677829     42.819514
2               New York   -74.012359     40.731043   -73.990798     40.756703
3             Mamaroneck   -73.757999     40.921536   -73.713686     40.980429
4               Brooklyn   -74.002144     40.644119   -73.970419     40.680033
...                  ...          ...           ...          ...           ...
119760            Groton   -76.523685     42.529700   -76.263208     42.631687
119761  Long Island City   -73.962795     40.727849   -73.909813     40.763086
119762         Ridgewood   -73.923920     40.682447   -73.852145     40.714176
119763  Long Island City   -73.962795     40.727849   -73.909813     40.763086
119764          New York   -73.955778     40.782531   -73.930891     40.800665

[119765 rows x 5 columns]

In [ ]:
# check out the cortland geo

dtypes= {
      'cb_BASENAME' : str,
      'cb_BLKGRP' : str,
      'cb_BLOCK' : str,
      'cb_GEOID' : str,
      'cb_TRACT' : str,
      'cb_COUNTY' : str,
      'cb_STATE' : str,
      'cnty_COUNTY' : str,
      'cnty_STATE' : str,
      'cong_BASENAME' : str,
      'cntysub_COUSUB' : str,
      'cntysub_GEOID' : str,
      'inc_PLACE' : str,
      'centracts_TRACT' : str,
      'csa_GEOID' : str
      }

cortland_geo_df = pd.read_csv('/content/drive/My Drive/IRS_processed/cortland_geo_df.csv',
                              dtype=dtypes)
display(cortland_geo_df)



cntysub_NAME cntysub_GEOID
0         Cortland city    3602318388
1       Summerhill town    3601172037
2         Cortland city    3602318388
3    Cortlandville town    3602318421
4         Cortland city    3602318388
..                  ...           ...
119  Cortlandville town    3602318421
120         Virgil town    3602377596
121         Virgil town    3602377596
122       Cortland city    3602318388
123         Virgil town    3602377596

[124 rows x 2 columns]

In [ ]:
#TODO: in most cases, need to set index=false when saving csv
bmf_cities_df = pd.read_csv(proc_dir + 'bmf_cities_df_precensus.csv')
display(bmf_cities_df)
bmf_cities_df.info()

#ny_cities_df = pd.read_csv('/content/drive/My Drive/IRS_processed/ny_cities_p_df.csv')
#display(ny_cities_df)

Unnamed: 0    major_city         uszip_county       inc_tot  np_cnt  \
0              0      New York      New York County  2.967132e+11   20896   
1              1      Brooklyn         Kings County  2.284092e+10   15084   
2              2         Bronx         Bronx County  1.628941e+10    3971   
3              3       Buffalo          Erie County  1.060585e+10    3837   
4              4     Rochester        Monroe County  1.615948e+10    2753   
...          ...           ...                  ...           ...     ...   
1517        1517        Helena  St. Lawrence County  0.000000e+00       1   
1518        1518  Harpersfield      Delaware County  0.000000e+00       1   
1519        1519       Harford      Cortland County  0.000000e+00       1   
1520        1520   South Byron       Genesee County  1.574590e+05       1   
1521        1521   Southfields        Orange County  7.622600e+04       1   

      inc_rank  nbr_np_rank  inc_rank_seq  np_cnt_rank_seq  
0          1.0          1.0             1                1  
1          3.0          2.0             3                2  
2          4.0          3.0             4                3  
3          8.0          4.0             8                4  
4          5.0          5.0             5                5  
...        ...          ...           ...              ...  
1517    1359.0       1432.0          1437             1518  
1518    1359.0       1432.0          1435             1519  
1519    1359.0       1432.0          1433             1520  
1520    1163.0       1432.0          1163             1521  
1521    1268.0       1432.0          1268             1522  

[1522 rows x 9 columns]

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1522 entries, 0 to 1521
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Unnamed: 0       1522 non-null   int64  
 1   major_city       1522 non-null   object 
 2   uszip_county     1522 non-null   object 
 3   inc_tot          1522 non-null   float64
 4   np_cnt           1522 non-null   int64  
 5   inc_rank         1522 non-null   float64
 6   nbr_np_rank      1522 non-null   float64
 7   inc_rank_seq     1522 non-null   int64  
 8   np_cnt_rank_seq  1522 non-null   int64  
dtypes: float64(3), int64(4), object(2)
memory usage: 107.1+ KB


# Google Data Commons

In [ ]:
# Install datacommons_pandas
!pip install datacommons_pandas --quiet
!pip install datacommons --quiet


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.8/45.8 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.5/46.5 kB 4.1 MB/s eta 0:00:00


In [ ]:
import datacommons_pandas as dc
dc.set_api_key(userdata.get('data_commons_key'))


In [ ]:

dc.get_stat_value('geoId/3600155', "Count_Person")

city_geoId = 'geoId/3600155'
dc.get_property_values([city_geoId], "name")

county = dc.get_property_values([city_geoId], 'containedInPlace')[city_geoId]
print (county)

#quick tests
dc.get_stat_value("geoId/05", "Count_Person_Male")
dc.get_stat_value("geoId/3601172037", "Count_Person")
dc.get_stat_all(["geoId/3601172037"], ["Count_Person", "Count_Person_Male"])


In [ ]:
# @title test data commons on just cortland NPs

# Note:   the census geocode on just the subset of local nonprofits
# returns did lookup county subdivision geoid, which can be used
# against google data commons.

# check collection of geoid from census load
flds = ['cntysub_NAME', 'cntysub_GEOID']
cortland_geo_df[flds]

# cortland_geo_df.info()

geoid_list = cortland_geo_df[flds].to_numpy().tolist()
display(geoid_list)

print (type(geoid_list ))
geoid_list[1]
geoid_list[1][0]

for i in geoid_list:
  print (i[0], i[1])


In [ ]:
# use google data commons from census geoid in cntysub_GEOID
def apply_people_cnt(cousub):
  geoId = 'geoId/' + cousub
  return dc.get_stat_value(geoId, "Count_Person")

cortland_geo_df['dc_Count_Person'] = cortland_geo_df['cntysub_GEOID'].apply(apply_people_cnt)


In [ ]:
# how to get the county, knowing the city

In [ ]:
# @title Get Cities and Populations with Data Commons
# https://github.com/datacommonsorg/api-python/blob/master/notebooks/analyzing_census_data.ipynb

#  dc.set_api_key(userdata.get('data_commons_key'))

#TODO:  future: in might be more efficient to first get counties
#       then get cities in county, instead of current - looking up
#       counties after getting cities

ny_dcid = 'geoId/36'  # geoId/36 represents the state of New York

cities = dc.get_places_in([ny_dcid], 'City')[ny_dcid]
cities_df = dc.build_multivariate_dataframe(cities, ['Count_Person', 'Median_Age_Person'])

#TODO: future:  opportunity to collect more demographics...
# nothing returned on perArea...
#cities_df = dc.build_multivariate_dataframe(cities, ['Count_Person', 'Median_Age_Person', 'Count_Person_PerArea'])

#display(cities_df)

cities_df['dc_all_names'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'name'))
cities_df['dc_name'] = cities_df['dc_all_names'].str[0]
cities_df['dc_name'] = cities_df['dc_name'].str.replace(', New York', '')
cities_df['dc_name'] = cities_df['dc_name'].str.replace(' (town)', '')

# display(cities_df)

#from property labels
# usCensusGeoId
#'latitude',
#'longitude',
#'musicbrainzAreaId',
#fips553
#wikidataId

cities_df['dc_usCensusGeoId'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'usCensusGeoId'))
cities_df['dc_latitude'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'latitude'))
cities_df['dc_longitude'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'longitude'))
cities_df['dc_musicbrainzAreaId'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'musicbrainzAreaId'))
cities_df['dc_fips553'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'fips553'))
cities_df['dc_wikidataId'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'wikidataId'))

# woops, lists

cities_df['dc_usCensusGeoId'] = cities_df['dc_usCensusGeoId'].str[0]
cities_df['dc_latitude'] = cities_df['dc_latitude'].str[0]
cities_df['dc_longitude'] = cities_df['dc_longitude'].str[0]
cities_df['dc_musicbrainzAreaId'] = cities_df['dc_musicbrainzAreaId'].str[0]
cities_df['dc_fips553'] = cities_df['dc_fips553'].str[0]
cities_df['dc_wikidataId'] = cities_df['dc_wikidataId'].str[0]

# display(cities_df)

# woops, I wanted counties

cities_df['dc_contained'] = cities_df.index.map(dc.get_property_values(cities_df.index, 'containedInPlace'))

display(cities_df)

#cities_df.info() # 2192


Count_Person  Median_Age_Person  \
place                                                 
geoId/3512529            33576.0                NaN   
geoId/3600155              573.0               51.7   
geoId/3600199             1633.0               36.3   
geoId/3600232             1492.0               54.9   
geoId/3600276             1561.0               31.5   
...                          ...                ...   
wikidataId/Q941325        2000.0                NaN   
wikidataId/Q94791         7493.0                NaN   
wikidataId/Q969032        3840.0                NaN   
wikidataId/Q970821        6500.0                NaN   
wikidataId/Q970933        9706.0                NaN   

                                              dc_all_names       dc_name  \
place                                                                      
geoId/3512529                                     [Carmel]        Carmel   
geoId/3600155                                     [Accord]        Accord   
geoId/3600199                                      [Adams]         Adams   
geoId/3600232                               [Adams Center]  Adams Center   
geoId/3600276       [Addison, Addison (village), New York]       Addison   
...                                                    ...           ...   
wikidataId/Q941325                              [Stamford]      Stamford   
wikidataId/Q94791              [Allegany (town), New York]      Allegany   
wikidataId/Q969032            [Yorkshire (town), New York]     Yorkshire   
wikidataId/Q970821                               [Corinth]       Corinth   
wikidataId/Q970933                                 [Alden]         Alden   

                    dc_usCensusGeoId      dc_latitude      dc_longitude  \
place                                                                     
geoId/3512529                    NaN           41.385  -73.729444444444   
geoId/3600155       1600000US3600155  41.791111111111  -74.228888888889   
geoId/3600199       1600000US3600199          43.8092        -76.022978   
geoId/3600232       1600000US3600232  43.862222222222        -75.988663   
geoId/3600276       1600000US3600276        42.106321         -77.23199   
...                              ...              ...               ...   
wikidataId/Q941325               NaN  42.416666666667  -74.616666666667   
wikidataId/Q94791                NaN         42.09278         -78.49472   
wikidataId/Q969032               NaN         42.48953          -78.4881   
wikidataId/Q970821               NaN  43.226666666667  -73.889722222222   
wikidataId/Q970933               NaN             42.9  -78.490833333333   

                                    dc_musicbrainzAreaId dc_fips553  \
place                                                                 
geoId/3512529       3078c9ef-fc87-4407-b899-12ef1dd84cc3   35-12529   
geoId/3600155                                        NaN   36-00155   
geoId/3600199                                        NaN   36-00199   
geoId/3600232                                        NaN   36-00232   
geoId/3600276                                        NaN   36-00276   
...                                                  ...        ...   
wikidataId/Q941325                                   NaN        NaN   
wikidataId/Q94791                                    NaN        NaN   
wikidataId/Q969032                                   NaN        NaN   
wikidataId/Q970821                                   NaN        NaN   
wikidataId/Q970933                                   NaN        NaN   

                   dc_wikidataId                        dc_contained  
place                                                                 
geoId/3512529           Q1013504                       [geoId/36079]  
geoId/3600155           Q2489840  [geoId/36, geoId/36111, zip/12404]  
geoId/3600199           Q3461972  [geoId/36, geoId/36045, zip/13605]  
geoId/3600232           Q1812896  [geoId/36, geoId/36045, zi

In [ ]:
# @title Split "contained" into county and zip
# the contained often returns multiple geoIds.
# Need to split into appropriate columns - county and zip
# hm, must be an easier way, but just gonna do a def

def do_zip(c3):
  if len(c3) == 0:
    return None
  else:
    # ok, check entry for what it is
    for y in range(len(c3)):
      geo_type, geo_id = c3[y].split('/')
      #print (c3, geo_type, geo_id)
      if geo_type == "zip":
        return geo_id

cities_df['dc_zip'] = cities_df['dc_contained'].apply(do_zip)


def do_contained(c3):
  if len(c3) == 0:
    return None
  else:
    # ok, check entry for what it is
    for y in range(len(c3)):
      geo_type, geo_id = c3[y].split('/')
      #print (c3, geo_type, geo_id)
      if geo_type == "geoId" and len(geo_id) == 5:
        return c3[y]

cities_df['dc_county'] = cities_df['dc_contained'].apply(do_contained)

display(cities_df)



Count_Person  Median_Age_Person  \
place                                                 
geoId/3512529            33576.0                NaN   
geoId/3600155              573.0               51.7   
geoId/3600199             1633.0               36.3   
geoId/3600232             1492.0               54.9   
geoId/3600276             1561.0               31.5   
...                          ...                ...   
wikidataId/Q941325        2000.0                NaN   
wikidataId/Q94791         7493.0                NaN   
wikidataId/Q969032        3840.0                NaN   
wikidataId/Q970821        6500.0                NaN   
wikidataId/Q970933        9706.0                NaN   

                                              dc_all_names       dc_name  \
place                                                                      
geoId/3512529                                     [Carmel]        Carmel   
geoId/3600155                                     [Accord]        Accord   
geoId/3600199                                      [Adams]         Adams   
geoId/3600232                               [Adams Center]  Adams Center   
geoId/3600276       [Addison, Addison (village), New York]       Addison   
...                                                    ...           ...   
wikidataId/Q941325                              [Stamford]      Stamford   
wikidataId/Q94791              [Allegany (town), New York]      Allegany   
wikidataId/Q969032            [Yorkshire (town), New York]     Yorkshire   
wikidataId/Q970821                               [Corinth]       Corinth   
wikidataId/Q970933                                 [Alden]         Alden   

                    dc_usCensusGeoId      dc_latitude      dc_longitude  \
place                                                                     
geoId/3512529                    NaN           41.385  -73.729444444444   
geoId/3600155       1600000US3600155  41.791111111111  -74.228888888889   
geoId/3600199       1600000US3600199          43.8092        -76.022978   
geoId/3600232       1600000US3600232  43.862222222222        -75.988663   
geoId/3600276       1600000US3600276        42.106321         -77.23199   
...                              ...              ...               ...   
wikidataId/Q941325               NaN  42.416666666667  -74.616666666667   
wikidataId/Q94791                NaN         42.09278         -78.49472   
wikidataId/Q969032               NaN         42.48953          -78.4881   
wikidataId/Q970821               NaN  43.226666666667  -73.889722222222   
wikidataId/Q970933               NaN             42.9  -78.490833333333   

                                    dc_musicbrainzAreaId dc_fips553  \
place                                                                 
geoId/3512529       3078c9ef-fc87-4407-b899-12ef1dd84cc3   35-12529   
geoId/3600155                                        NaN   36-00155   
geoId/3600199                                        NaN   36-00199   
geoId/3600232                                        NaN   36-00232   
geoId/3600276                                        NaN   36-00276   
...                                                  ...        ...   
wikidataId/Q941325                                   NaN        NaN   
wikidataId/Q94791                                    NaN        NaN   
wikidataId/Q969032                                   NaN        NaN   
wikidataId/Q970821                                   NaN        NaN   
wikidataId/Q970933                                   NaN        NaN   

                   dc_wikidataId                        dc_contained dc_zip  \
place                                                                         
geoId/3512529           Q1013504                       [geoId/36079]   None   
geoId/3600155           Q2489840  [geoId/36, geoId/36111, zip/12404]  12404   
geoId/3600199           Q3461972  [geoId/36, geoId/36045, zip/13605]  13605   
geoId/3600232       

In [ ]:
# @title Get County Name from geoId
# with county geoIds,can add county names

cities_df['dc_county_name'] = cities_df['dc_county'].map(dc.get_property_values(cities_df['dc_county'], 'name'))
cities_df['dc_county_name'] = cities_df['dc_county_name'].str[0]

display(cities_df)


Count_Person  Median_Age_Person  \
place                                                 
geoId/3512529            33576.0                NaN   
geoId/3600155              573.0               51.7   
geoId/3600199             1633.0               36.3   
geoId/3600232             1492.0               54.9   
geoId/3600276             1561.0               31.5   
...                          ...                ...   
wikidataId/Q941325        2000.0                NaN   
wikidataId/Q94791         7493.0                NaN   
wikidataId/Q969032        3840.0                NaN   
wikidataId/Q970821        6500.0                NaN   
wikidataId/Q970933        9706.0                NaN   

                                              dc_all_names       dc_name  \
place                                                                      
geoId/3512529                                     [Carmel]        Carmel   
geoId/3600155                                     [Accord]        Accord   
geoId/3600199                                      [Adams]         Adams   
geoId/3600232                               [Adams Center]  Adams Center   
geoId/3600276       [Addison, Addison (village), New York]       Addison   
...                                                    ...           ...   
wikidataId/Q941325                              [Stamford]      Stamford   
wikidataId/Q94791              [Allegany (town), New York]      Allegany   
wikidataId/Q969032            [Yorkshire (town), New York]     Yorkshire   
wikidataId/Q970821                               [Corinth]       Corinth   
wikidataId/Q970933                                 [Alden]         Alden   

                    dc_usCensusGeoId      dc_latitude      dc_longitude  \
place                                                                     
geoId/3512529                    NaN           41.385  -73.729444444444   
geoId/3600155       1600000US3600155  41.791111111111  -74.228888888889   
geoId/3600199       1600000US3600199          43.8092        -76.022978   
geoId/3600232       1600000US3600232  43.862222222222        -75.988663   
geoId/3600276       1600000US3600276        42.106321         -77.23199   
...                              ...              ...               ...   
wikidataId/Q941325               NaN  42.416666666667  -74.616666666667   
wikidataId/Q94791                NaN         42.09278         -78.49472   
wikidataId/Q969032               NaN         42.48953          -78.4881   
wikidataId/Q970821               NaN  43.226666666667  -73.889722222222   
wikidataId/Q970933               NaN             42.9  -78.490833333333   

                                    dc_musicbrainzAreaId dc_fips553  \
place                                                                 
geoId/3512529       3078c9ef-fc87-4407-b899-12ef1dd84cc3   35-12529   
geoId/3600155                                        NaN   36-00155   
geoId/3600199                                        NaN   36-00199   
geoId/3600232                                        NaN   36-00232   
geoId/3600276                                        NaN   36-00276   
...                                                  ...        ...   
wikidataId/Q941325                                   NaN        NaN   
wikidataId/Q94791                                    NaN        NaN   
wikidataId/Q969032                                   NaN        NaN   
wikidataId/Q970821                                   NaN        NaN   
wikidataId/Q970933                                   NaN        NaN   

                   dc_wikidataId                        dc_contained dc_zip  \
place                                                                         
geoId/3512529           Q1013504                       [geoId/36079]   None   
geoId/3600155           Q2489840  [geoId/36, geoId/36111, zip/12404]  12404   
geoId/3600199           Q3461972  [geoId/36, geoId/36045, zip/13605]  13605   
geoId/3600232       

In [ ]:
# check data types in cities_df
cities_df.info() # 2192

# could change lat lng to float
dc_latitude           2190 non-null   object
dc_longitude          2190 non-null   object


<class 'pandas.core.frame.DataFrame'>
Index: 2192 entries, geoId/3600155 to geoId/3660411
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Count_Person          2021 non-null   float64
 1   Median_Age_Person     1315 non-null   float64
 2   dc_all_names          2192 non-null   object 
 3   dc_name               2190 non-null   object 
 4   dc_usCensusGeoId      1299 non-null   object 
 5   dc_latitude           2190 non-null   object 
 6   dc_longitude          2190 non-null   object 
 7   dc_musicbrainzAreaId  236 non-null    object 
 8   dc_fips553            1691 non-null   object 
 9   dc_wikidataId         1889 non-null   object 
 10  dc_contained          2192 non-null   object 
 11  dc_zip                699 non-null    object 
 12  dc_county             2107 non-null   object 
 13  dc_county_name        2107 non-null   object 
dtypes: float64(2), object(12)
memory usage: 321.4+ KB


In [ ]:
# Since I'm matching on city/town name, have to be unique

# what names are duplicated
cities_df.groupby('dc_name').filter(lambda x: len(x) > 1).sort_values(by=['dc_name']).head(50)


print ( len(cities_df.groupby('dc_name').filter(lambda x: len(x) > 1)) ) #643

# city and county duplicated
cities_df.groupby(['dc_name', 'dc_county_name'] ).filter(lambda x: len(x) > 1).sort_values(by=['dc_name']).head(50)

print (len(cities_df.groupby(['dc_name', 'dc_county_name'] ).filter(lambda x: len(x) > 1)) ) #463

# lacking a better strategy, just get max populate for each city and county
#

# Sort the DataFrame by city, county, and population in descending order.
cities_df.sort_values(by=['dc_name', 'dc_county_name', 'Count_Person'],
                      ascending=[True, False, False], inplace=True)

# Remove duplicates, keeping the first occurrence, highest pop after sorting).
cities_df.drop_duplicates(subset=['dc_name', 'dc_county_name'], keep='first', inplace=True)

cities_df.shape # (1958, 14)
print (len(cities_df.groupby(['dc_name', 'dc_county_name'] ).filter(lambda x: len(x) > 1)) ) #0





0


## Match pruned data commons cities to bmf cities



In [ ]:
bmf_cities_df.info() #1522
cities_df.info() #1958
# layering in demogs to see_match_df

cities_df.reset_index(inplace=True)

cities_df.rename(columns={'place': 'dc_place'}, inplace=True)
display(cities_df)


see_match_df = bmf_cities_df.merge(
    cities_df,
    how='left',
    left_on=['major_city', 'uszip_county'],
    right_on=['dc_name', 'dc_county_name']
)

display(see_match_df)

# how many didn't match
see_match_df['dc_name'].isna().sum() #455

#which ones
filt = see_match_df['dc_name'].isna()
see_match_df[filt]


455

# Get Census Geography that (roughly) matches major city

Note:  These census api routines work, but onone day kept timing out in google colab.  The same URLs returned data fast in browser and the same code worked fine when the run from my local machine (with vscode).

There 1522 unique cities in dataset for all New York.


### Census: acs5 county subdivision

#### Census API 2022 acs5 county subdivision

In [ ]:

#  Using Census api to get population for county subdvisions (towns, villages)

# https://api.census.gov/data/2022/acs/acs5
# get=NAME,B01001_001E&
#for=county%20subdivision:*&in=state:36&in=county:*
# when using county subdivision, rows = 1023

# Note: previous experiments linking BMF city names to census didn't work
# presumably due to inconsistencies in city name.
# by getting the census civil minor from uszipcodes seems to make match possible

# https://api.census.gov/data/2022/acs/acs5?get=NAME,B01001_001E&for=county%20subdivision:*&in=state:36&in=county:*


api_key = userdata.get('census_api_key')

#base_url = 'https://api.census.gov/data/2022/acs/acs5'

#params = {
#    'get': 'NAME,B01001_001E',
#    'for': 'county_subdivision:*',
#    'in': 'state:36',
#    'in': 'county:*',
#    'key': api_key
#}

params = {'key': api_key}

# other variables to get:https://api.census.gov/data/2022/acs/acs5/variables.html
url = 'https://api.census.gov/data/2022/acs/acs5?get=NAME,B01001_001E&for=county%20subdivision:*&in=state:36&in=county:*'

response = requests.get(url, params=params)
data = response.json()
print (data)

#TODO: make subdivision a string when loading
# df = pd.DataFrame(data, dtype={'A': 'int32', 'B': 'string'})

if response.status_code == 200:
    data = response.json()
    # Convert to pandas DataFrame
    columns = data[0]
    cnty_sub_df = pd.DataFrame(data[1:], columns=columns)

#else:
#    print(f"Error: {response.status_code}")




[['NAME', 'B01001_001E', 'state', 'county', 'county subdivision'], ['Albany city, Albany County, New York', '99692', '36', '001', '01000'], ['Berne town, Albany County, New York', '2695', '36', '001', '06211'], ['Bethlehem town, Albany County, New York', '35039', '36', '001', '06354'], ['Coeymans town, Albany County, New York', '7253', '36', '001', '16694'], ['Cohoes city, Albany County, New York', '17960', '36', '001', '16749'], ['Colonie town, Albany County, New York', '85406', '36', '001', '17343'], ['Green Island town, Albany County, New York', '2968', '36', '001', '30532'], ['Guilderland town, Albany County, New York', '36932', '36', '001', '31104'], ['Knox town, Albany County, New York', '2679', '36', '001', '40002'], ['New Scotland town, Albany County, New York', '9087', '36', '001', '50672'], ['Rensselaerville town, Albany County, New York', '1798', '36', '001', '61181'], ['Watervliet city, Albany County, New York', '10325', '36', '001', '78674'], ['Westerlo town, Albany County

In [ ]:
# Save or Read from csv, so I don't have to hit census again

# if loading from drive
dtypes = {'county' : str,
        'county subdivision' : str,
        'B01001_001E' : int}

cnty_sub_df = pd.read_csv(proc_dir + 'cnty_sub_df.csv', dtype=dtypes)
display(cnty_sub_df)

cnty_sub_df.info()

#cnty_sub_df.drop(columns=['Unnamed: 0.1'], inplace=True)
display(cnty_sub_df)

display(cnty_sub_df) # 1023


# if loaded from census api run,
# save output so I don't have hit census
cnty_sub_df.to_csv(proc_dir + 'cnty_sub_df.csv', index=False)

# check
filt = cnty_sub_df['NAME'].str.contains('ayette')
display(cnty_sub_df[filt])


#### Prep and Prune

In [ ]:
# Prep cnty_sub_df

# do not see how to get NAME with city, County, State into seperate cols direct from census, so dividing
cnty_sub_df[['cnty_sub_name', 'county', 'state']] = cnty_sub_df['NAME'].str.split(',', n=0, expand=True)

# removing city, town
cnty_sub_df['cnty_sub_name'] = cnty_sub_df['cnty_sub_name'].str.replace(' city', '')
cnty_sub_df['cnty_sub_name'] = cnty_sub_df['cnty_sub_name'].str.replace(' town', '')
cnty_sub_df['cnty_sub_name'] = cnty_sub_df['cnty_sub_name'].str.replace(' borough', '')
cnty_sub_df['cnty_sub_name'] = cnty_sub_df['cnty_sub_name'].str.title()


cnty_sub_df.rename( columns={'state': 'cnty_sub_state'}, inplace=True)
cnty_sub_df.rename( columns={'county': 'cnty_sub_county'}, inplace=True)

# change datatype of column census_df['B01001_001E'] to integer
# cnty_sub_df['B01001_001E'] = cnty_sub_df['B01001_001E'].astype(int)

cnty_sub_df.rename( columns={'B01001_001E': 'cnty_sub_B01001_001E'}, inplace=True)
cnty_sub_df.rename( columns={'Unnamed: 0': 'cnty_sub_o_ind'}, inplace=True)
display(cnty_sub_df)

#filt = cnty_sub_df['NAME'].str.contains('ayette')
#display(cnty_sub_df[filt])



cnty_sub_o_ind                                     NAME  \
0                  0     Albany city, Albany County, New York   
1                  1      Berne town, Albany County, New York   
2                  2  Bethlehem town, Albany County, New York   
3                  3   Coeymans town, Albany County, New York   
4                  4     Cohoes city, Albany County, New York   
...              ...                                      ...   
1018            1018   Middlesex town, Yates County, New York   
1019            1019        Milo town, Yates County, New York   
1020            1020      Potter town, Yates County, New York   
1021            1021     Starkey town, Yates County, New York   
1022            1022      Torrey town, Yates County, New York   

      cnty_sub_B01001_001E cnty_sub_state cnty_sub_county county subdivision  \
0                    99692       New York   Albany County              01000   
1                     2695       New York   Albany County              06211   
2                    35039       New York   Albany County              06354   
3                     7253       New York   Albany County              16694   
4                    17960       New York   Albany County              16749   
...                    ...            ...             ...                ...   
1018                  1261       New York    Yates County              47020   
1019                  6847       New York    Yates County              47504   
1020                  1876       New York    Yates County              59597   
1021                  3393       New York    Yates County              70816   
1022                  1355       New York    Yates County              75055   

     cnty_sub_name  
0           Albany  
1            Berne  
2        Bethlehem  
3         Coeymans  
4           Cohoes  
...            ...  
1018     Middlesex  
1019          Milo  
1020        Potter  
1021       Starkey  
1022        Torrey  

[1023 rows x 7 columns]

In [ ]:
# since i'm matching on names and counties, the city/county has to be unique

# which cities are duplicated, 92
cnty_sub_df.groupby('cnty_sub_name').filter(lambda x: len(x) > 1).sort_values(by=['cnty_sub_name']).head(50)

flds= ['NAME', 'cnty_sub_B01001_001E',  'cnty_sub_name', 'cnty_sub_county']
# cities and counties duplicated
(cnty_sub_df[flds].groupby(['cnty_sub_name', 'cnty_sub_county'])
      .filter(lambda x: len(x) > 1)
      .sort_values(by=['cnty_sub_name', 'cnty_sub_county'])
      .head(50)
)
#Note: quick review, when name is the city, it's the larger population
# didn't count, but often there must be a town within a city both with same name
Example:
363 	Batavia city, Genesee County, New York 	15510 	Batavia 	Genesee County
364 	Batavia town, Genesee County, New York 	6309 	Batavia 	Genesee County

# before deduping, curious about Albion and Geneva
cnty_sub_df[cnty_sub_df['cnty_sub_name'] == 'Albion']
# one row in Orleans, another row in Oswego county


cnty_sub_df[cnty_sub_df['cnty_sub_name'] == 'Geneva']
# 3 rows a town and city in one county,another row with 0 population in another county
# wikipedia: Geneva is a city in Ontario and Seneca counties in the U.S. state of New York.

# Sort the DataFrame by city, county, pop(pop in descending order)
(cnty_sub_df.sort_values(by=['cnty_sub_name', 'cnty_sub_county', 'cnty_sub_B01001_001E'],
                         ascending=[True, False, False],
                         inplace=True)
)

# Remove duplicates, keeping the first occurrence (which will have the largest 'B01001_001E' after sorting).
cnty_sub_df.drop_duplicates(subset=['cnty_sub_name', 'cnty_sub_county'], keep='first', inplace=True)

# verify one city/town
(cnty_sub_df.groupby(['cnty_sub_name', 'cnty_sub_county'])
        .filter(lambda x: len(x) > 1)
        .sort_values(by=['cnty_sub_name', 'cnty_sub_county'])
        .head(50)
) #0

# verify it got the highest population
filt = cnty_sub_df['cnty_sub_name'].isin(['Albion', 'Amsterdam', 'Geneva', 'Waddington', 'Watertown'])
cnty_sub_df[filt]

cnty_sub_df.info() #999

# note: another way to get max over a group
#idx = df.groupby('group')['value'].idxmax()
# Get the rows corresponding to the maximum values
#result = df.loc[idx]



<class 'pandas.core.frame.DataFrame'>
Index: 999 entries, 420 to 997
Data columns (total 7 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   cnty_sub_o_ind        999 non-null    int64 
 1   NAME                  999 non-null    object
 2   cnty_sub_B01001_001E  999 non-null    int64 
 3   cnty_sub_state        999 non-null    object
 4   cnty_sub_county       999 non-null    object
 5   county subdivision    999 non-null    object
 6   cnty_sub_name         999 non-null    object
dtypes: int64(2), object(5)
memory usage: 62.4+ KB


#### Match to Cities (see_match_df)

In [ ]:
# try to match county subdivsions to city list

# see_match_df already combines bmf_cities and data commons.
print ("See Match Rows:  ", len(see_match_df) )
print ("bmf cities Rows:", len(bmf_cities_df)) #1522
print ("cnty_sub Rows:  ", len(cnty_sub_df)) # 999

See Match Rows:   1522
bmf cities Rows: 1522
cnty_sub Rows:   999


#Hm, it seems spaces got into these values
cnty_sub_df[['cnty_sub_name', 'cnty_sub_county']]
see_match_df[['major_city', 'uszip_county']]

cnty_sub_df['cnty_sub_county'] = cnty_sub_df['cnty_sub_county'].str.strip()
cnty_sub_df['cnty_sub_name'] = cnty_sub_df['cnty_sub_name'].str.strip()

# just in case
see_match_df['major_city'] = see_match_df['major_city'].str.strip()
see_match_df['uszip_county'] = see_match_df['uszip_county'].str.strip()

# verify
filt = cnty_sub_df['cnty_sub_county'] == 'Monroe County'
cnty_sub_df[filt]

filt = cnty_sub_df['cnty_sub_county'].str.contains('Jefferson')
cnty_sub_df[filt]

filt = cnty_sub_df['cnty_sub_name'] == 'Adams'
cnty_sub_df[filt]

#Monroe County

# get all entries from cities and the matching cities in census county subdivision
#see_match_df = city_cnty_df.merge(cnty_sub_df, how='left', left_on='major_city', right_on='county_sub_name')

# layering in demogs to see_match_df
see_match_df = see_match_df.merge(cnty_sub_df,
                                   how='left',
                                   left_on=['major_city', 'uszip_county'],
                                   right_on=['cnty_sub_name', 'cnty_sub_county']
                                   )

display(see_match_df)  # 1522

see_match_df.info()

# woops, fix, try again
#see_match_df.drop(columns=['cnty_sub_o_ind', 'NAME',  'cnty_sub_B01001_001E', 'cnty_sub_state', 'cnty_sub_county', 'county subdivision', 'cnty_sub_name'], inplace=True)
#display(see_match_df)

#how many didn't match?
see_match_df['cnty_sub_name'].isna().sum() # 997
see_match_df['cnty_sub_name'].notna().sum() # 525
# ok, total is 1522
# Of the 1522 entries in in the df city list, 997 did not match to census subdivisions (by name)

# check some of the ones that didn't match, just in case
filt = see_match_df['cnty_sub_name'].isna()
display(see_match_df[filt])






Unnamed: 0    major_city         uszip_county       inc_tot  np_cnt  \
0              0      New York      New York County  2.967132e+11   20896   
1              1      Brooklyn         Kings County  2.284092e+10   15084   
2              2         Bronx         Bronx County  1.628941e+10    3971   
3              3       Buffalo          Erie County  1.060585e+10    3837   
4              4     Rochester        Monroe County  1.615948e+10    2753   
...          ...           ...                  ...           ...     ...   
1517        1517        Helena  St. Lawrence County  0.000000e+00       1   
1518        1518  Harpersfield      Delaware County  0.000000e+00       1   
1519        1519       Harford      Cortland County  0.000000e+00       1   
1520        1520   South Byron       Genesee County  1.574590e+05       1   
1521        1521   Southfields        Orange County  7.622600e+04       1   

      inc_rank  nbr_np_rank  inc_rank_seq  np_cnt_rank_seq       dc_place  \
0          1.0          1.0             1                1            NaN   
1          3.0          2.0             3                2            NaN   
2          4.0          3.0             4                3            NaN   
3          8.0          4.0             8                4  geoId/3611000   
4          5.0          5.0             5                5  geoId/3663000   
...        ...          ...           ...              ...            ...   
1517    1359.0       1432.0          1437             1518            NaN   
1518    1359.0       1432.0          1435             1519  geoId/3632281   
1519    1359.0       1432.0          1433             1520  geoId/3632160   
1520    1163.0       1432.0          1163             1521            NaN   
1521    1268.0       1432.0          1268             1522            NaN   

      Count_Person  Median_Age_Person    dc_all_names       dc_name  \
0              NaN                NaN             NaN           NaN   
1              NaN                NaN             NaN           NaN   
2              NaN                NaN             NaN           NaN   
3         278349.0               33.9       [Buffalo]       Buffalo   
4         211328.0               32.9     [Rochester]     Rochester   
...            ...                ...             ...           ...   
1517           NaN                NaN             NaN           NaN   
1518        1442.0                NaN  [Harpersfield]  Harpersfield   
1519         943.0                NaN       [Harford]       Harford   
1520           NaN                NaN             NaN           NaN   
1521           NaN                NaN             NaN           NaN   

      dc_usCensusGeoId      dc_latitude      dc_longitude  \
0                  NaN              NaN               NaN   
1                  NaN              NaN               NaN   
2                  NaN              NaN               NaN   
3     1600000US3611000        42.892492  -78.849444444444   
4     1600000US3663000  43.165555555556  -77.611388888889   
...                ...              ...               ...   
1517               NaN              NaN               NaN   
1518               NaN  42.438333333333          -74.6875   
1519               NaN  42.426111111111  -76.226666666667   
1520               NaN              NaN               NaN   
1521               NaN              NaN               NaN   

                      dc_musicbrainzAreaId dc_fips553 dc_wikidataId  \
0                                      NaN        NaN           NaN   
1                                      NaN        NaN           NaN   
2                                      NaN        NaN           NaN   
3     7e5e7fd7-c1eb-4cb8-87e2-fb1c0eda9e48   36-11000        Q40435   
4     17203e02-355a-40db-a524-980192eb9d0f   36-63000        Q49218   
...                                    ...        ...           ...   
1517                                   NaN        NaN           NaN   
15

In [ ]:
# Misc Checks

# research a few cites that didn't match to census subdivisons
Flushing
Pyrites
Helena

filt = cnty_sub_df['NAME'].str.contains('elena')
filt = cnty_sub_df['county_sub_name'].str.contains('elena')
display(cnty_sub_df[filt])
# wikipdia: Helena is a hamlet in the Town of Brasher in St. Lawrence County, New York, United States.

# Brasher is in cnty sub
# so hamlets are prob in subdivisions
filt = cnty_sub_df['NAME'].str.contains('Brasher')
filt = cnty_sub_df['cnty_sub_name'].str.contains('Brasher')
display(cnty_sub_df[filt])

#Pyrites
filt = cnty_sub_df['NAME'].str.contains('Pyrites')
filt = cnty_sub_df['county_sub_name'].str.contains('Pyrites')
display(cnty_sub_df[filt])
# wikipdia: Pyrites is a hamlet in St. Lawrence County, New York, United States.
# The community is located along the Grasse River, 5.7 miles (9.2 km) south of Canton.
# Pyrites has a post office with ZIP code 13677


#Flushing
filt = cnty_sub_df['NAME'].str.contains('lushing')
#filt = cnty_sub_df['county_sub_name'].str.contains('Flushing')
display(cnty_sub_df[filt])
# wikipedia: Flushing is a neighborhood in the north-central portion of the New York City borough of Queens.

filt = cnty_sub_df['NAME'].str.contains('Crittenden')
cnty_sub_df[filt]
filt = city_cnty_df['major_city'].str.contains('Crittenden')
display(city_cnty_df[filt])
# wikipedia:Crittenden is a small hamlet in the town of Alden in Erie County, New York

cnty_sub_df.info()

# big places
filt= cnty_sub_df['B01001_001E'] > 1000000
display(cnty_sub_df[filt])

filt = see_match_df['major_city'].str.contains('New York')
display(see_match_df[filt])

filt = cnty_sub_df['county_sub_name'].str.contains('New York')
display(cnty_sub_df[filt])

# looks like the boros are divided, but no new york city in census...?
# perhaps add to census combined statistal areas
#filt = cnty_sub_df['B01001_001E'] > 500000

# cnty_sub_df[filt]

# ones that match
filt = see_match_df['major_city'].str.contains('Albany')
display(see_match_df[filt])
# city pop matches wikipedia

filt = see_match_df['cnty_sub_name'].notna()
see_match_df[filt].head(50)



Unnamed: 0        major_city        uszip_county       inc_tot  np_cnt  \
1             1          Brooklyn        Kings County  2.284092e+10   15084   
2             2             Bronx        Bronx County  1.628941e+10    3971   
3             3           Buffalo         Erie County  1.060585e+10    3837   
4             4         Rochester       Monroe County  1.615948e+10    2753   
5             5            Albany       Albany County  1.534299e+10    2163   
6             6     Staten Island     Richmond County  2.059546e+09    1680   
7             7          Syracuse     Onondaga County  7.508000e+09    1451   
11           11            Ithaca     Tompkins County  1.304681e+10     848   
12           12       Schenectady  Schenectady County  4.899644e+09     750   
14           14           Yonkers  Westchester County  1.569346e+09     611   
15           15      White Plains  Westchester County  1.533774e+09     598   
16           16        Binghamton       Broome County  2.005985e+09     514   
18           18            Monroe       Orange County  3.516372e+08     496   
19           19      Poughkeepsie     Dutchess County  3.289074e+09     495   
22           22              Troy   Rensselaer County  1.975041e+09     424   
23           23      New Rochelle  Westchester County  1.274995e+09     415   
25           25  Saratoga Springs     Saratoga County  1.180070e+09     377   
26           26      Mount Vernon  Westchester County  1.614994e+08     363   
28           28         Scarsdale  Westchester County  3.899541e+08     340   
30           30          Kingston       Ulster County  1.133185e+09     323   
31           31             Utica       Oneida County  1.727990e+09     319   
36           36        Huntington      Suffolk County  2.531015e+08     309   
39           39            Elmira      Chemung County  6.805149e+08     292   
41           41          Newburgh       Orange County  5.796168e+08     286   
42           42        Middletown       Orange County  1.046317e+09     283   
43           43     Niagara Falls      Niagara County  2.944495e+08     278   
44           44         Hempstead       Nassau County  1.059366e+09     277   
45           45           Norwich     Chenango County  1.707260e+08     275   
46           46         Jamestown   Chautauqua County  2.798706e+08     272   
49           49      Clifton Park     Saratoga County  8.797027e+07     253   
52           52         Watertown    Jefferson County  7.538365e+08     245   
53           53            Auburn       Cayuga County  5.021379e+08     239   
54           54          Lockport      Niagara County  1.394759e+08     236   
55           55         Pittsford       Monroe County  2.241206e+08     228   
57           57           Webster       Monroe County  3.260954e+08     223   
69           69           Oneonta       Otsego County  4.031691e+08     205   
74           74       Plattsburgh      Clinton County  6.058014e+08     202   
75           75               Rye  Westchester County  3.806445e+08     200   
83           83              Rome       Oneida County  2.988706e+08     187   
85           85      East Hampton      Suffolk County  2.894750e+08     185   
87           87            Oswego       Oswego County  2.902729e+08     185   
90           90      Orchard Park         Erie County  4.709754e+08     181   
91           91       Glens Falls       Warren County  1.303006e+08     181   
92           92       Canandaigua      Ontario County  3.425010e+08     180   
94           94            Hudson     Columbia County  1.521611e+08     177   
95           95           Hamburg         Erie County  6.396335e+07     177   
97           97         Smithtown      Suffolk County  5.913096e+08     174   
98           98        Long Beach       Nassau County  1.061575e+08     173   
99           99         Riverhead      Suffolk County  5.082958e+08     167   
101         101            Vestal       Broome County  

### Census: 2020/dec/pl

In [ ]:
# Not Used
# try other tables, geography
# https://api.census.gov/data/2020/dec/pl/geography.json


from google.colab import userdata
API_KEY = userdata.get('census_api_key')

# Set the state FIPS code for New York (36)
state_code = "36"

# Base URL for the API
base_url = "https://api.census.gov/data/2020/dec/pl"

# Function to get county subdivisions (which includes minor civil divisions) for New York State
# Set parameters for the API request
params = {
    'get': 'NAME',
    #'for': 'county subdivision:*',   # 1023
    'for': 'subminor civil division:*', #unknown/unsupported geography hierarchy
    'in': f'state:{state_code}',
    'key': API_KEY
}

# Make the API request
response = requests.get(base_url, params=params)

# Check if the request was successful
if response.status_code == 200:
    data = response.json()
    # Convert to pandas DataFrame
    columns = data[0]
    #population_data = pd.DataFrame(data[1:], columns=columns)
    dec_df = pd.DataFrame(data[1:], columns=columns)

else:
  print (response.text)
  print(f"Error: Unable to fetch data. Status code {response.status_code}")

error: unknown/unsupported geography hierarchy
Error: Unable to fetch data. Status code 400


In [ ]:
dec_df.info()
display(dec_df)

NAME state county  \
0          Allen town, Allegany County, New York    36    003   
1          Amity town, Allegany County, New York    36    003   
2       Birdsall town, Allegany County, New York    36    003   
3       Caneadea town, Allegany County, New York    36    003   
4     Friendship town, Allegany County, New York    36    003   
...                                          ...   ...    ...   
1018       Inlet town, Hamilton County, New York    36    041   
1019   Long Lake town, Hamilton County, New York    36    041   
1020   Morehouse town, Hamilton County, New York    36    041   
1021       Wells town, Hamilton County, New York    36    041   
1022      Danube town, Herkimer County, New York    36    043   

     county subdivision  
0                 01319  
1                 02011  
2                 06717  
3                 12243  
4                 27705  
...                 ...  
1018              37495  
1019              43412  
1020              48340  
1021              79059  
1022              19686  

[1023 rows x 4 columns]

### Census: acs5 for places and county

#### Census API

In [ ]:
# using census acs5 to get demographics
# tweaked "for" to do places and counties seperately
#TODO:can add more demo vars beyone the B01001_001E
# acs5 ny places
# 1294 places
# 62 counties

import requests
import pandas as pd

# Replace this with your Census API key
API_KEY = userdata.get('census_api_key')

# Census API base URL for ACS 5-Year estimates, 2022
base_url = 'https://api.census.gov/data/2022/acs/acs5'

#variables = ['B01001_001E', 'B01001_002E', 'B01001_026E']  # Total population, Male, Female

# Set the parameters for the API request
params = {
    'get': 'NAME,B01001_001E',  # Variables and place names
    #'for': 'place:*',  # All places (cities, towns, villages)
    'for': 'county:*',  # All places (cities, towns, villages)
    'in': 'state:36',  # New York State FIPS code is 36
    'key': API_KEY
}

# Make the API request
response = requests.get(base_url, params=params, timeout=10)
print("response url:   ", response.url)

# Check if the request was successful
if response.status_code == 200:
    data = response.json()
    # Convert the JSON data to a pandas DataFrame
    columns = data[0]
    #acs5_place_df = pd.DataFrame(data[1:], columns=columns)
    acs5_cnty_df = pd.DataFrame(data[1:], columns=columns)
else:
    print (response.url)
    print(f"Error: Unable to fetch data. Status code {response.status_code}")



response url:    https://api.census.gov/data/2022/acs/acs5?get=NAME%2CB01001_001E&for=county%3A%2A&in=state%3A36&key=c4dd4253d7612ea36d9b19e4ef12b5742268a4c3


#### Prep Counties and add to see_match_df
Note: see_match will become bmf_cities

In [ ]:
# save or read county demographics

# save it
acs5_cnty_df.to_csv(proc_dir + 'acs5_cnty_df.csv', index=False)

# read it
dtypes= {'B01001_001E' : int,
         'county' : str}
acs5_cnty_df = pd.read_csv(proc_dir + "acs5_cnty_df.csv", dtype=dtypes)
display(acs5_cnty_df) #62

acs5_cnty_df.info()


NAME  B01001_001E  state county
0        Albany County, New York       315041     36    001
1      Allegany County, New York        47222     36    003
2         Bronx County, New York      1443229     36    005
3        Broome County, New York       198365     36    007
4   Cattaraugus County, New York        77000     36    009
..                           ...          ...    ...    ...
57   Washington County, New York        61310     36    115
58        Wayne County, New York        91324     36    117
59  Westchester County, New York       997904     36    119
60      Wyoming County, New York        40338     36    121
61        Yates County, New York        24713     36    123

[62 rows x 4 columns]

In [ ]:
#setup columns to merge into a city dataframe
acs5_cnty_df[['county_name', 'state_name']] = acs5_cnty_df['NAME'].str.split(',', n=0, expand=True)
# display(acs5_cnty_df)

acs5_cnty_df.rename( columns={'B01001_001E': 'cnty_B01001_001E'}, inplace=True)
acs5_cnty_df.rename( columns={'state': 'state_fips'}, inplace=True)
acs5_cnty_df.rename( columns={'county': 'cnty_fips'}, inplace=True)
acs5_cnty_df.drop(columns=['NAME'], inplace=True)

display(acs5_cnty_df) #62

cnty_B01001_001E  state_fips cnty_fips         county_name state_name
0             315041          36       001       Albany County   New York
1              47222          36       003     Allegany County   New York
2            1443229          36       005        Bronx County   New York
3             198365          36       007       Broome County   New York
4              77000          36       009  Cattaraugus County   New York
..               ...         ...       ...                 ...        ...
57             61310          36       115   Washington County   New York
58             91324          36       117        Wayne County   New York
59            997904          36       119  Westchester County   New York
60             40338          36       121      Wyoming County   New York
61             24713          36       123        Yates County   New York

[62 rows x 5 columns]

In [ ]:
# add county totals to each city in the county

see_match_df
pd.set_option('display.max_rows', 100)
display(acs5_cnty_df)

see_match_df = see_match_df.merge(acs5_cnty_df, how='left', left_on='uszip_county', right_on='county_name')
display(see_match_df)

# did they all match?
print(see_match_df['county_name'].isna().sum())
# TODO: st. lawrence needs to get fixed in the df
filt = see_match_df['county_name'].isna()
display(see_match_df[filt])
# update uszip count to add period to St Lawrence


3


#### Prep Places, add to see match

In [ ]:
# acs place

#acs5_place_df.to_csv(proc_dir + 'acs5_place_df.csv', index=False)

dtypes= {'B01001_001E' : int,
         'state' : str,
         'place' : str}

fn = proc_dir + "acs5_place_df.csv"
acs5_place_df = pd.read_csv(fn, dtype=dtypes)
display(acs5_place_df) #1293
# https://en.wikipedia.org/wiki/List_of_municipalities_in_New_York

NAME  B01001_001E state  place
0               Accord CDP, New York          350    36  00155
1            Adams village, New York         1923    36  00199
2         Adams Center CDP, New York         1022    36  00232
3          Addison village, New York         1841    36  00276
4            Afton village, New York         1159    36  00342
...                              ...          ...   ...    ...
1288         Yorkshire CDP, New York         1057    36  84044
1289  Yorktown Heights CDP, New York         2147    36  84088
1290     Yorkville village, New York         2635    36  84099
1291    Youngstown village, New York         1965    36  84143
1292              Zena CDP, New York          726    36  84187

[1293 rows x 4 columns]

In [ ]:
#TODO: rename use city to acs5_place_city
acs5_place_df['acs5_city'] = acs5_place_df['NAME'].str.replace(', New York', '')

acs5_place_df['acs5_city'] = acs5_place_df['acs5_city'].str.replace(' CDP', '')
acs5_place_df['acs5_city'] = acs5_place_df['acs5_city'].str.replace(' village', '')
acs5_place_df['acs5_city'] = acs5_place_df['acs5_city'].str.replace(' town', '')
acs5_place_df['acs5_city'] = acs5_place_df['acs5_city'].str.replace(' borough', '')
acs5_place_df['acs5_city'] = acs5_place_df['acs5_city'].str.replace(' city', '')
acs5_place_df['acs5_city'] = acs5_place_df['acs5_city'].str.title()

display(acs5_place_df)


NAME  B01001_001E state  place  \
0               Accord CDP, New York          350    36  00155   
1            Adams village, New York         1923    36  00199   
2         Adams Center CDP, New York         1022    36  00232   
3          Addison village, New York         1841    36  00276   
4            Afton village, New York         1159    36  00342   
...                              ...          ...   ...    ...   
1288         Yorkshire CDP, New York         1057    36  84044   
1289  Yorktown Heights CDP, New York         2147    36  84088   
1290     Yorkville village, New York         2635    36  84099   
1291    Youngstown village, New York         1965    36  84143   
1292              Zena CDP, New York          726    36  84187   

             acs5_city  
0               Accord  
1                Adams  
2         Adams Center  
3              Addison  
4                Afton  
...                ...  
1288         Yorkshire  
1289  Yorktown Heights  
1290         Yorkville  
1291        Youngstown  
1292              Zena  

[1293 rows x 5 columns]

In [ ]:
# review, then prune

# -- review
display(acs5_place_df)

acs5_place_df['acs5_city'].value_counts().head(50)

filt = acs5_place_df['acs5_city'] == 'Northville'
acs5_place_df[filt]

# https://en.wikipedia.org/wiki/List_of_municipalities_in_New_York#T
filt = acs5_place_df['acs5_city'].isin(['Adams', 'Syracuse', 'Stamford', 'Tonawanda', 'Troy', 'Whitehall'])
acs5_place_df[filt]

acs5_place_df['use_city'].count()  # 1293

acs5_place_df.groupby(['use_city']).count() # 1289

# which cities are duplicated
acs5_place_df.groupby('use_city').filter(lambda x: len(x) > 1)

#806 	Northville village, New York 	1034 	36 	53770 	Northville
#807 	Northville CDP, New York 	1829 	36 	53775 	Northville
#955 	Riverside village, New York 	594 	36 	62061 	Riverside
#956 	Riverside CDP, New York 	2945 	36 	62066 	Riverside
#1141 	Tuckahoe CDP, New York 	1200 	36 	75572 	Tuckahoe
#1142 	Tuckahoe village, New York 	6995 	36 	75583 	Tuckahoe
#1272 	Woodbury CDP, New York 	9169 	36 	82744 	Woodbury
#1273 	Woodbury village, New York 	11371 	36 	82750 	Woodbury





NAME  B01001_001E state  place   acs5_city
806  Northville village, New York         1034    36  53770  Northville
807      Northville CDP, New York         1829    36  53775  Northville

In [ ]:
# -- prune

# in dataframe acs5_place_df, find duplicates of use_city
# and keep the one with largest value in B01001_001E

# Sort the DataFrame by 'use_city' and 'B01001_001E' in descending order.
acs5_place_df.sort_values(by=['acs5_city', 'B01001_001E'], ascending=[True, False], inplace=True)

# Remove duplicates, keeping the first occurrence (which will have the largest 'B01001_001E' after sorting).
acs5_place_df.drop_duplicates(subset=['acs5_city'], keep='first', inplace=True)

acs5_place_df.groupby('acs5_city').filter(lambda x: len(x) > 1)

acs5_place_df.rename( columns={'B01001_001E': 'place_B01001_001E'}, inplace=True)
acs5_place_df.rename( columns={'NAME': 'acs5_name'}, inplace=True)
acs5_place_df.rename( columns={'place': 'acs5_place_fips'}, inplace=True)
acs5_place_df

display(acs5_place_df) # 1289

acs5_place_df.info() # 1289



<class 'pandas.core.frame.DataFrame'>
Index: 1289 entries, 0 to 1292
Data columns (total 5 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   acs5_name          1289 non-null   object
 1   place_B01001_001E  1289 non-null   int64 
 2   state              1289 non-null   object
 3   acs5_place_fips    1289 non-null   object
 4   acs5_city          1289 non-null   object
dtypes: int64(1), object(4)
memory usage: 60.4+ KB


#### Add Places to Match

In [ ]:
display(acs5_place_df)

# layering

# add the matches to see_matches (already has cnty_sub_df)

see_match_df = see_match_df.merge(acs5_place_df, how='left', left_on='major_city', right_on='acs5_city')
display(see_match_df)


flds = ['major_city', 'Count_Person', 'dc_name',
        'cnty_sub_B01001_001E', 'cnty_sub_name',
        'place_B01001_001E', 'acs5_city', 'acs5_name'
        ]

see_match_df[flds]

see_match_df[['major_city', 'uszip_county',
              'dc_name', 'Count_Person',
        'cnty_sub_B01001_001E', 'cnty_sub_name',
        'place_B01001_001E', 'acs5_city', 'acs5_name'
              ]]



major_city  Count_Person       dc_name  cnty_sub_B01001_001E  \
0         New York           NaN           NaN                   NaN   
1         Brooklyn           NaN           NaN             2679620.0   
2            Bronx           NaN           NaN             1443229.0   
3          Buffalo      278349.0       Buffalo              276688.0   
4        Rochester      211328.0     Rochester              210992.0   
...            ...           ...           ...                   ...   
1517        Helena           NaN           NaN                   NaN   
1518  Harpersfield        1442.0  Harpersfield                1472.0   
1519       Harford         943.0       Harford                 923.0   
1520   South Byron           NaN           NaN                   NaN   
1521   Southfields           NaN           NaN                   NaN   

     cnty_sub_name  place_B01001_001E  acs5_city                 acs5_name  
0              NaN          8622467.0   New York   New York city, New York  
1         Brooklyn                NaN        NaN                       NaN  
2            Bronx                NaN        NaN                       NaN  
3          Buffalo           276688.0    Buffalo    Buffalo city, New York  
4        Rochester           210992.0  Rochester  Rochester city, New York  
...            ...                ...        ...                       ...  
1517           NaN                NaN        NaN                       NaN  
1518  Harpersfield                NaN        NaN                       NaN  
1519       Harford                NaN        NaN                       NaN  
1520           NaN                NaN        NaN                       NaN  
1521           NaN                NaN        NaN                       NaN  

[1522 rows x 8 columns]

###  Finalize Match

In [ ]:
# with tidied acs5_place_df, see if it matches cities

see_match_df[['major_city', 'uszip_county',
              'dc_name', 'Count_Person',
              'cnty_sub_name', 'cnty_sub_B01001_001E',
              'acs5_city', 'acs5_name', 'place_B01001_001E',
              ]]


# choose which population to use
# pass the row to def and compare

def pick_population(row):
    if not pd.isna(row['cnty_sub_B01001_001E']):
      return row['cnty_sub_B01001_001E']
    elif not pd.isna(row['place_B01001_001E']):
      return row['place_B01001_001E']
    elif not pd.isna(row['Count_Person']):
      return row['Count_Person']
    else:
      return None

def get_pop_src(row):
    if not pd.isna(row['cnty_sub_B01001_001E']):
      return "Census ACS5 County Subdivision"
    elif not pd.isna(row['place_B01001_001E']):
      return "Census ACS5 Places"
    elif not pd.isna(row['Count_Person']):
      return "Google Data Commons"
    else:
      return None


see_match_df['city_population'] = see_match_df.apply(pick_population, axis=1)
see_match_df['city_pop_src'] = see_match_df.apply(get_pop_src, axis=1)

# check
see_match_df

# save matches
see_match_df.to_csv(proc_dir + 'see_matches.csv')

see_match_df
see_match_df['city_population'].isna().sum() # 429

filt = see_match_df['city_population'].isna()
see_match_df[filt]

# cities that don't match
#6 	Staten Island
#8 	Flushing
#9 	Jamaica
#20 	Astoria
#27 	Long Island City
#34 	Queens Village
#37 	Forest Hills
#38 	Far Rockaway
#49 	Clifton Park



Unnamed: 0        major_city         uszip_county       inc_tot  np_cnt  \
8              8          Flushing        Queens County  3.297948e+09    1148   
9              9           Jamaica        Queens County  2.140089e+09    1033   
20            20           Astoria        Queens County  8.740210e+08     459   
27            27  Long Island City        Queens County  1.576563e+09     354   
34            34    Queens Village        Queens County  1.100832e+08     311   
...          ...               ...                  ...           ...     ...   
1514        1514           Howells        Orange County  0.000000e+00       1   
1515        1515           Pyrites  St. Lawrence County  1.000000e+00       1   
1517        1517            Helena  St. Lawrence County  0.000000e+00       1   
1520        1520       South Byron       Genesee County  1.574590e+05       1   
1521        1521       Southfields        Orange County  7.622600e+04       1   

      inc_rank  nbr_np_rank  inc_rank_seq  np_cnt_rank_seq dc_place  \
8         11.0          9.0            11                9      NaN   
9         14.0         10.0            14               10      NaN   
20        39.0         21.0            39               21      NaN   
27        22.0         28.0            22               28      NaN   
34       177.0         35.0           177               35      NaN   
...        ...          ...           ...              ...      ...   
1514    1359.0       1432.0          1440             1515      NaN   
1515    1356.0       1432.0          1358             1516      NaN   
1517    1359.0       1432.0          1437             1518      NaN   
1520    1163.0       1432.0          1163             1521      NaN   
1521    1268.0       1432.0          1268             1522      NaN   

      Count_Person  Median_Age_Person dc_all_names dc_name dc_usCensusGeoId  \
8              NaN                NaN          NaN     NaN              NaN   
9              NaN                NaN          NaN     NaN              NaN   
20             NaN                NaN          NaN     NaN              NaN   
27             NaN                NaN          NaN     NaN              NaN   
34             NaN                NaN          NaN     NaN              NaN   
...            ...                ...          ...     ...              ...   
1514           NaN                NaN          NaN     NaN              NaN   
1515           NaN                NaN          NaN     NaN              NaN   
1517           NaN                NaN          NaN     NaN              NaN   
1520           NaN                NaN          NaN     NaN              NaN   
1521           NaN                NaN          NaN     NaN              NaN   

     dc_latitude dc_longitude dc_musicbrainzAreaId dc_fips553 dc_wikidataId  \
8            NaN          NaN                  NaN        NaN           NaN   
9            NaN          NaN                  NaN        NaN           NaN   
20           NaN          NaN                  NaN        NaN           NaN   
27           NaN          NaN                  NaN        NaN           NaN   
34           NaN          NaN                  NaN        NaN           NaN   
...          ...          ...                  ...        ...           ...   
1514         NaN          NaN                  NaN        NaN           NaN   
1515         NaN          NaN                  NaN        NaN           NaN   
1517         NaN          NaN                  NaN        NaN           NaN   
1520         NaN          NaN                  NaN        NaN           NaN   
1521         NaN          NaN                  NaN        NaN           NaN   

     dc_contained dc_zip dc_county dc_county_name  cnty_sub_o_ind NAME  \
8             NaN    NaN       NaN            NaN             NaN  NaN   
9             NaN    NaN       NaN            NaN             NaN  NaN   
20            NaN    NaN       NaN            NaN           

## Save bmf_cities_p_df

In [ ]:
# save the bmf_cities_p_df

bmf_cities_p_df = see_match_df.copy()

display(bmf_cities_p_df)

# woops
bmf_cities_p_df.drop(columns=['Unnamed: 0',
                              ], inplace=True)
display(bmf_cities_p_df)

bmf_cities_p_df.info()

bmf_cities_p_df.to_csv(proc_dir + 'bmf_cities_p_df.csv', index=False)

## Misc Research

In [ ]:
# obsolete
#ok, cateogories

            cnty sub  acs5    dc
1:          null      null                  431 the ones that don't have match - research
2:          X         null                  546
3:          null      X                     171
4:          X         X                     374  check to see if pops are equal

# case 4: manual review suggests just use county subdivision

does get expected total, 1522
1091 should have a match

filt = see_match_df['use_city'].isna() & see_match_df['county_sub_name'].isna()
case1 = len(see_match_df[filt])

filt = see_match_df['use_city'].notna() & see_match_df['county_sub_name'].isna()
case2 = len(see_match_df[filt])

filt = see_match_df['use_city'].isna() & see_match_df['county_sub_name'].notna()
case3 = len(see_match_df[filt])

filt = see_match_df['use_city'].notna() & see_match_df['county_sub_name'].notna()
case4 = len(see_match_df[filt])

print (case1, case2, case3, case4)
431 546 171 374

see_match_df.rename( columns={'Unnamed: 0': 'cnty_sub_ind'}, inplace=True)
display(see_match_df)

# look at ones without a match, case 1

filt = see_match_df['use_city'].isna() & see_match_df['county_sub_name'].isna()
see_match_df[filt].head(50)

filt = see_match_df['use_city'].isna()
see_match_df[filt]['major_city'].head(50)

see_match_df['use_city'].isna().sum() #602 didn't match

filt = see_match_df['major_city'].str.contains('Ithaca')
see_match_df[filt]


In [ ]:
# test: compare populations returned between cnty sub and places

flds = ['major_city', 'county subdivision', 'county_sub_name',
        'cnty_sub_B01001_001E',
        'county subdivision', 'place_B01001_001E',
        'place', 'use_city']

filt = see_match_df['use_city'].notna() & see_match_df['county_sub_name'].notna() & (see_match_df['cnty_sub_B01001_001E'] != see_match_df['place_B01001_001E'])
#filt +=
see_match_df[filt][flds]



major_city county subdivision county_sub_name  cnty_sub_B01001_001E  \
18          Monroe              47999          Monroe               21240.0   
19    Poughkeepsie              59652    Poughkeepsie               45390.0   
36      Huntington              37000      Huntington              203808.0   
41        Newburgh              50045        Newburgh               31808.0   
44       Hempstead              34000       Hempstead              789763.0   
...            ...                ...             ...                   ...   
1361          York              84022            York                3198.0   
1402        Gorham              29531          Gorham                4114.0   
1425      Lorraine              43544        Lorraine                 951.0   
1496        Altona              01583          Altona                2446.0   
1497     Ellisburg              24086       Ellisburg                3382.0   

     county subdivision  place_B01001_001E  place      use_city  
18                47999             9420.0  47988        Monroe  
19                59652            31717.0  59641  Poughkeepsie  
36                37000            19610.0  36233    Huntington  
41                50045            28751.0  50034      Newburgh  
44                34000            58557.0  33139     Hempstead  
...                 ...                ...    ...           ...  
1361              84022              345.0  84011          York  
1402              29531              474.0  29520        Gorham  
1425              43544              114.0  43533      Lorraine  
1496              01583              657.0  01572        Altona  
1497              24086              188.0  24075     Ellisburg  

[316 rows x 8 columns]

#### When subdivisions don't match, use place

In [ ]:
# case 3
      cnty_sub_df acs5_place
3:      null      X     171

# update dataframe see_match_df from acs5_place_cd when see_match_df.county_sub_name is null and major_city matches


acs5_place_df.info()

# Assuming 'place' in acs5_place_df is acs5_place_cd
filtered_see_match_df = see_match_df[see_match_df['county_sub_name'].isna()]
filtered_see_match_df = filtered_see_match_df.merge(
    acs5_place_df[['use_city', 'place', 'place_B01001_001E']],
    how='left',
    left_on='major_city',
    right_on='use_city'
)

# Update the original see_match_df
see_match_df.update(filtered_see_match_df)

<class 'pandas.core.frame.DataFrame'>
Index: 1289 entries, 0 to 1292
Data columns (total 5 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   NAME               1289 non-null   object
 1   place_B01001_001E  1289 non-null   int64 
 2   state              1289 non-null   object
 3   place              1289 non-null   object
 4   use_city           1289 non-null   object
dtypes: int64(1), object(4)
memory usage: 60.4+ KB


## other census tests

In [ ]:

u = 'https://api.census.gov/data/2022/acs/acs5?get=NAME,B01001_001E&for=place:*&in=state:36&key=c4dd4253d7612ea36d9b19e4ef12b5742268a4c3'


response = requests.get(u, timeout=30)
print("response url:   ", response.url)

# Check if the request was successful
if response.status_code == 200:
    print("response 2url:   ", response.url)
    data = response.json()
    # Convert the JSON data to a pandas DataFrame
    columns = data[0]
    acs5_place_df = pd.DataFrame(data[1:], columns=columns)

else:
    print (response.url)
    print(f"Error: Unable to fetch data. Status code {response.status_code}")

print("response 3url:   ", response.url)






ConnectTimeout: HTTPSConnectionPool(host='api.census.gov', port=443): Max retries exceeded with url: /data/2022/acs/acs5?get=NAME,B01001_001E&for=place:*&in=state:36&key=c4dd4253d7612ea36d9b19e4ef12b5742268a4c3 (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x79c76aac9840>, 'Connection to api.census.gov timed out. (connect timeout=30)'))

In [ ]:
# for census, place and consolidated city, get population

#https://api.census.gov/data/2022/acs/acs5/subject?get=NAME,S0101_C01_001E&for=place:*&in=state:36

# this got 1293, same as query for place
#https://api.census.gov/data/2022/acs/acs5/subject?get=NAME,S0101_C01_001E&for=place:*&in=state:36

# new york doesn't have consolidated city in geography
#https://api.census.gov/data/2022/acs/acs5/subject?get=NAME,S0101_C01_001E&for=consolidated%20city:*&in=state:*

from google.colab import userdata

API_KEY = userdata.get('census_api_key')

# Set the state FIPS code for New York (36)
state_code = "36"

base_url = "https://api.census.gov/data/2022/acs/acs5/subject"

# Set parameters for the API request
params = {
    'get': 'NAME,S0101_C01_001E',
    #'for': 'place:*',
    'for': 'consolidated_city:*',
    'in': f'state:{state_code}',
    'key': API_KEY
}

# Make the API request
response = requests.get(base_url, params=params)

# Check if the request was successful
if response.status_code == 200:
    data = response.json()
    # Convert to pandas DataFrame
    #columns = ['Subdivision_Name', 'state', 'county', 'place_cd']
    columns = ['cons_city_name', 'state', 'county', 'cons_city_cd']
    #place_data_df = pd.DataFrame(data[1:], columns=columns)
    cons_city_df = pd.DataFrame(data[1:], columns=columns)
else:
  print(f"Error: Unable to fetch data. Status code {response.status_code}")
  print (response.text)




Error: Unable to fetch data. Status code 400
error: unknown/unsupported geography hierarchy


In [ ]:

display(place_data_df)



Subdivision_Name state county place_cd
0               Accord CDP, New York   350     36    00155
1            Adams village, New York  1923     36    00199
2         Adams Center CDP, New York  1022     36    00232
3          Addison village, New York  1841     36    00276
4            Afton village, New York  1159     36    00342
...                              ...   ...    ...      ...
1288         Yorkshire CDP, New York  1057     36    84044
1289  Yorktown Heights CDP, New York  2147     36    84088
1290     Yorkville village, New York  2635     36    84099
1291    Youngstown village, New York  1965     36    84143
1292              Zena CDP, New York   726     36    84187

[1293 rows x 4 columns]

### from census FTP


In [ ]:
# Use file from census FTP:

dtypes = {'PLACE' : str,
          'COUSUB' : str}

fn = proc_dir + "sub-est2022_36.csv"
#sub_est_orig_df = pd.read_csv(fn)
sub_est_df = pd.read_csv(fn)
display(sub_est_df)


SUMLEV  STATE  COUNTY  PLACE  COUSUB  CONCIT  PRIMGEO_FLAG FUNCSTAT  \
0         40     36       0      0       0       0             0        A   
1        162     36       0    199       0       0             0        A   
2        162     36       0    276       0       0             0        A   
3        162     36       0    342       0       0             0        A   
4        162     36       0    408       0       0             0        A   
...      ...    ...     ...    ...     ...     ...           ...      ...   
3401      71     36     123  21050   70816       0             1        A   
3402      71     36     123  99990   70816       0             1        F   
3403      61     36     123      0   75055       0             0        A   
3404      71     36     123  20896   75055       0             1        A   
3405      71     36     123  99990   75055       0             1        F   

                         NAME    STNAME  ESTIMATESBASE2020  POPESTIMATE2020  \
0                    New York  New York           20201230         20108296   
1               Adams village  New York               1693             1688   
2             Addison village  New York               1605             1601   
3               Afton village  New York                798              797   
4             Airmont village  New York              10130            10059   
...                       ...       ...                ...              ...   
3401           Dundee village  New York               1724             1718   
3402  Balance of Starkey town  New York               1677             1673   
3403              Torrey town  New York               1297             1292   
3404          Dresden village  New York                298              297   
3405   Balance of Torrey town  New York                999              995   

      POPESTIMATE2021  POPESTIMATE2022  
0            19857492         19677151  
1                1698             1687  
2                1587             1575  
3                 791              790  
4               10112            10104  
...               ...              ...  
3401             1709             1693  
3402             1675             1668  
3403             1283             1275  
3404              293              292  
3405              990              983  

[3406 rows x 14 columns]

In [ ]:

sub_est_df['use_city'] = sub_est_df['NAME']
sub_est_df['use_city'] = sub_est_df['use_city'].str.replace(' (pt.)', '')
sub_est_df['use_city'] = sub_est_df['use_city'].str.replace(' village', '')
sub_est_df['use_city'] = sub_est_df['use_city'].str.replace(' town', '')
sub_est_df['use_city'] = sub_est_df['use_city'].str.replace(' borough', '')
sub_est_df['use_city'] = sub_est_df['use_city'].str.replace(' city', '')
sub_est_df['use_city'] = sub_est_df['use_city'].str.title()

sub_est_df.info()  # 3406
display(sub_est_df.head(50))

sub_est_df.sort_values(by=['use_city'])





SUMLEV  STATE  COUNTY  PLACE  COUSUB  CONCIT  PRIMGEO_FLAG FUNCSTAT  \
0       40     36       0      0       0       0             0        A   
1      162     36       0    199       0       0             0        A   
2      162     36       0    276       0       0             0        A   
3      162     36       0    342       0       0             0        A   
4      162     36       0    408       0       0             0        A   
5      162     36       0    441       0       0             0        A   
6      162     36       0   1000       0       0             0        A   
7      162     36       0   1033       0       0             0        A   
8      162     36       0   1088       0       0             0        A   
9      162     36       0   1154       0       0             0        A   
10     162     36       0   1187       0       0             0        A   
11     162     36       0   1198       0       0             0        A   
12     162     36       0   1286       0       0             0        A   
13     162     36       0   1440       0       0             0        A   
14     162     36       0   1517       0       0             0        A   
15     162     36       0   1737       0       0             0        A   
16     162     36       0   2044       0       0             0        A   
17     162     36       0   2066       0       0             0        A   
18     162     36       0   2143       0       0             0        A   
19     162     36       0   2176       0       0             0        A   
20     162     36       0   2198       0       0             0        A   
21     162     36       0   2286       0       0             0        A   
22     162     36       0   2407       0       0             0        A   
23     162     36       0   2506       0       0             0        A   
24     162     36       0   2550       0       0             0        A   
25     162     36       0   2583       0       0             0        A   
26     162     36       0   2737       0       0             0        A   
27     162     36       0   2902       0       0             0        A   
28     162     36       0   2968       0       0             0        A   
29     162     36       0   3001       0       0             0        A   
30     162     36       0   3078       0       0             0        A   
31     162     36       0   3188       0       0             0        A   
32     162     36       0   3331       0       0             0        A   
33     162     36       0   3353       0       0             0        A   
34     162     36       0   3408       0       0             0        A   
35     162     36       0   4033       0       0             0        A   
36     162     36       0   4198       0       0             0        A   
37     162     36       0   4253       0       0             0        A   
38     162     36       0   4440       0       0             0        A   
39     162     36       0   4715       0       0             0        A   
40     162     36       0   4759       0       0             0        A   
41     162     36       0   4803       0       0             0        A   
42     162     36       0   5034       0       0             0        A   
43     162     36       0   5100       0       0             0        A   
44     162     36       0   5639       0       0             0        A   
45     162     36       0   5672       0       0             0        A   
46     162     36       0   5771       0       0             0        A   
47     162     36       0   5815       0       0             0        A   
48     162     36       0   5848       0       0             0        A   
49     162     36       0   6046       0       0             0        A   

                      NAME    STNAME  ESTIMATESBASE2020  POPESTIMATE2020  \
0                 New York  New York           20201230         20108296   
1            Adams village

In [ ]:
# lookup summary levels
#sum_levels = sub_est_df['SUMLEV'].unique()
#for lvl in sum_levels:
#  print (lvl)

sum_lvl_lu =  {40 : 'state',
              50 : 'county',
              162 : 'Place (no CDPs)',
              157 : 'Place (no CDPs)-County',
              61 : 'MCD/CCD (10,000+)',
              71 : 'County Subdivision-Place (10,000+)/Remainder'
            }

#sub_est_df.info()
#print (sum_lvl_lu[157])

def get_sum_lvl(levl):
  return sum_lvl_lu[levl]

sub_est_df['sum_lvl_desc'] = sub_est_df['SUMLEV'].apply(get_sum_lvl)
display(sub_est_df)


# verify sum levels
filt = sub_est_df['sum_lvl_desc'] == 'county'
sub_est_df[filt]

# count by sum level codes
sub_est_df['sum_lvl_desc'].value_counts()



In [ ]:
# the places that should be cities, towns, villages
#              162 : 'Place (no CDPs)',
#              157 : 'Place (no CDPs)-County',
#              61 : 'MCD/CCD (10,000+)',
#              71 : 'County Subdivision-Place (10,000+)/Remainder'

sel_list = [162, 157, 61, 71]

filt = sub_est_df['SUMLEV'].isin(sel_list)
sub_est_df[filt]


SUMLEV  STATE  COUNTY  PLACE  COUSUB  CONCIT  PRIMGEO_FLAG FUNCSTAT  \
1        162     36       0    199       0       0             0        A   
1569      71     36      45    199     210       0             1        A   
1568      61     36      45      0     210       0             0        A   
1547     157     36      45    199       0       0             0        A   
2        162     36       0    276       0       0             0        A   
...      ...    ...     ...    ...     ...     ...           ...      ...   
595      162     36       0  84099       0       0             0        A   
2148      71     36      65  84099   81754       0             1        A   
2052      71     36      63  84143   59267       0             1        A   
2032     157     36      63  84143       0       0             0        A   
596      162     36       0  84143       0       0             0        A   

                    NAME    STNAME  ESTIMATESBASE2020  POPESTIMATE2020  \
1          Adams village  New York               1693             1688   
1569       Adams village  New York               1693             1688   
1568          Adams town  New York               4967             4948   
1547       Adams village  New York               1693             1688   
2        Addison village  New York               1605             1601   
...                  ...       ...                ...              ...   
595    Yorkville village  New York               2658             2653   
2148   Yorkville village  New York               2658             2653   
2052  Youngstown village  New York               1863             1859   
2032  Youngstown village  New York               1863             1859   
596   Youngstown village  New York               1863             1859   

      POPESTIMATE2021  POPESTIMATE2022    use_city  \
1                1698             1687       Adams   
1569             1698             1687       Adams   
1568             4979             4947       Adams   
1547             1698             1687       Adams   
2                1587             1575     Addison   
...               ...              ...         ...   
595              2631             2607   Yorkville   
2148             2631             2607   Yorkville   
2052             1854             1850  Youngstown   
2032             1854             1850  Youngstown   
596              1854             1850  Youngstown   

                                      sum_lvl_desc  
1                                  Place (no CDPs)  
1569  County Subdivision-Place (10,000+)/Remainder  
1568                             MCD/CCD (10,000+)  
1547                        Place (no CDPs)-County  
2                                  Place (no CDPs)  
...                                            ...  
595                                Place (no CDPs)  
2148  County Subdivision-Place (10,000+)/Remainder  
2052  County Subdivision-Place (10,000+)/Remainder  
2032                        Place (no CDPs)-County  
596                                Place (no CDPs)  

[3343 rows x 16 columns]

In [ ]:
# quick check to see if census ftp file can fill gaps
# quick check
bmf_cities_p_df

filt = bmf_cities_p_df['city_population'].isna()
bmf_cities_p_df[filt]

print (len(bmf_cities_p_df))

filt = bmf_cities_p_df['city_population'].isna()
cities_no_pop = bmf_cities_p_df[filt]['major_city'].to_list()
#print(cities_no_pop)
print (len(cities_no_pop))  #429

filt = sub_est_df['use_city'].isin (cities_no_pop)
sub_est_df[filt]
# ok of all the cities without population, this sheet gives 3 more matches
# by major city name, anyway


# are any of these from bmfcities isin sub est
# ['Flushing', 'Jamaica', 'Astoria', 'Long Island City', 'Queens Village', 'Forest Hills'

filt = sub_est_df['use_city'] == 'Adams'
sub_est_df[filt]

filt = sub_est_df['use_city'] == 'Adams'
sub_est_df[filt]

filt = sub_est_df['use_city'] == 'Getszille'
sub_est_df[filt]


sub_est_df

filt = sub_est_df['use_city'].isin(cities_no_pop)
sub_est_df[filt]


SUMLEV  STATE  COUNTY  PLACE  COUSUB  CONCIT  PRIMGEO_FLAG FUNCSTAT  \
674       61     36       3      0   15990       0             1        A   
2503      61     36      79      0   39331       0             1        A   
2874      61     36     101      0    7740       0             1        A   

                  NAME    STNAME  ESTIMATESBASE2020  POPESTIMATE2020  \
674   Clarksville town  New York                971              969   
2503         Kent town  New York              12911            12905   
2874     Bradford town  New York                809              807   

      POPESTIMATE2021  POPESTIMATE2022     use_city  
674               964              960  Clarksville  
2503            12956            12903         Kent  
2874              801              795     Bradford

In [ ]:
# keep city/town names with largest population

display(sub_est_df)

# count dupes of use city at sum levels
# sub_est_df.groupby(['use_city', 'sum_lvl_desc']).count()

# multiple entries for city
sub_est_df.groupby('use_city').filter(lambda x: len(x) > 1)


sub_est_df[['NAME', 'use_city', 'SUMLEV', 'POPESTIMATE2022']].groupby('use_city').filter(lambda x: len(x) > 1)

# head
sub_est_df[['NAME', 'use_city', 'SUMLEV', 'POPESTIMATE2022']].groupby('use_city').filter(lambda x: len(x) > 1).head(50)



# see examples of dupes
filt = sub_est_df['use_city'] == 'Crittenden'
sub_est_df[filt]

# Adams 	4967
# Addison 2356
# Yorkville 2658

#.filter(lambda x: len(x) > 1)


# Sort the DataFrame by 'use_city', population, and census codes
#acs5_place_df.sort_values(by=['use_city', 'B01001_001E'], ascending=[True, False], inplace=True)

sub_est_df.sort_values(by=['use_city', 'POPESTIMATE2022', 'COUSUB', 'PLACE'],
                       ascending=[True, False, False, False],
                       inplace=True)

# Remove duplicates, keeping the first occurrence (which will have the largest population after sorting).
sub_est_df.drop_duplicates(subset=['use_city'], keep='first', inplace=True)


#sub_est_df.groupby('use_city').filter(lambda x: len(x) > 1)
# ---


Empty DataFrame
Columns: [SUMLEV, STATE, COUNTY, PLACE, COUSUB, CONCIT, PRIMGEO_FLAG, FUNCSTAT, NAME, STNAME, ESTIMATESBASE2020, POPESTIMATE2020, POPESTIMATE2021, POPESTIMATE2022, use_city, sum_lvl_desc]
Index: []

In [ ]:
# sub_est_df

# Brooklyn, Jamaica Crittenden Stow
filt= sub_est_orig_df['NAME'].str.contains('Crittenden')
sub_est_orig_df[filt]

filt = ny_cities_df['major_city'].str.contains('Crittenden')
ny_cities_df[filt]


display(ny_cities_df)
display(see_matches)

see_match2 = city_cnty_df.merge(sub_est_df, how='left', left_on='major_city', right_on='use_city')
display(see_match2)
see_match2[see_match2['use_city'].isna()] #


see_match2['use_city'].isna().sum() # 744




744

In [ ]:
filt = df['major_city'].str.contains('Crittenden')
df[filt]


EIN                                NAME             ICO  \
42310  161466207  CRITTENDEN VOLUNTARY FIRE DEPT INC  % NANCY FALKER   

                     STREET        CITY STATE         ZIP GROUP  SUBSECTION  \
42310  13415 GENESEE STREET  CRITTENDEN    NY  14038-0000  0000           3   

      AFFILIATION CLASSIFICATION  RULING  DEDUCTIBILITY FOUNDATION   ACTIVITY  \
42310           3           1000  199710              1         15  407000000   

      ORGANIZATION  STATUS TAX_PERIOD  ASSET_CD  INCOME_CD  FILING_REQ_CD  \
42310            1       1     202212         5          4              1   

       PF_FILING_REQ_CD  ACCT_PD  ASSET_AMT  INCOME_AMT  REVENUE_AMT NTEE_CD  \
42310                 0       12   928830.0    262616.0     234208.0    M24Z   

      SORT_NAME  p_org_id                                           ntee_cat  \
42310       NaN     42310  (M) Public Safety, Disaster Preparedness & Relief   

                                             ntee_define  class_cd_1  \
42310  Organizations that are responsible for the con...           1   

       class_cd_2  class_cd_3  class_cd_4  activity_cd_1  activity_cd_2  \
42310           0           0           0            407              0   

       activity_cd_3                                        act1_lu act2_lu  \
42310              0  Voluntary firemen's organization or auxiliary      na   

      act3_lu     RULE_DT       aff_lu       org_lu  \
42310      na  1997-10-01  Independent  Corporation   

                                  found_lu                  deduct_lu zipcode  \
42310  Receives support from Gov or Public  Contributions deductible.   14038   

      zipcode_type  major_city post_office_city common_city_list uszip_county  \
42310       PO BOX  Crittenden              NaN   ['Crittenden']  Erie County   

      state  radius_in_miles area_code_list  population  population_density  \
42310    NY              NaN            NaN         NaN                 NaN   

       land_area_in_sqmi  water_area_in_sqmi  housing_units  \
42310                NaN                 NaN            NaN   

       occupied_housing_units  median_home_value  median_household_income  \
42310                     NaN                NaN                      NaN   

       bounds_west  bounds_east  bounds_north  bounds_south  
42310          NaN          NaN           NaN           NaN

In [ ]:
# functstat definitions
# https://www.census.gov/library/reference/code-lists/functional-status-codes.html

# A,Active government providing primary general-purpose functions
# A,Active entity (federally recognized entities only)

import io
import pandas as pd
fstat_cd  = pd.read_csv(io.StringIO('''
funct_stat_cd,funct_stat_desc,fs_short_desc
A,Active government providing primary general-purpose functions, Active
B,Active government that is partially consolidated with another government but with separate officials providing primary general-purpose functions, Active partial consolidated
C,Active government consolidated with another government with a single set of officials, Active Consolidated
E,Active government providing special-purpose functions, Active special purpose
F,Active government that is subordinate to another unit of government, Active subordinate
F,Fictitious entity created to fill the Census Bureau geographic hierarchy, Fictitious
G,Active government that is subordinate to another unit of government, Active subordinate
H,Inactive government providing primary general-purpose functions, Inactive
I,Inactive governmental unit that has the power to provide primary special-purpose functions, Inactive special purpose
L,Inactive nonfunctioning legal real property entity with potential quasi-legal administrative functions, Inactive
M,Active legal real property entity with quasi-legal functions, Active legal real property
N,Nonfunctioning legal entity, Nonfunctioning legal
P,Active government providing special-purpose functions, Active special purpose
S,Statistical entity, Statistical
T,Active state-recognized entity, Active state recognized



'''), header=[0])


display(fstat_cd)


funct_stat_cd                                    funct_stat_desc  \
0              A  Active government providing primary general-pu...   
1              B  Active government that is partially consolidat...   
2              C  Active government consolidated with another go...   
3              E  Active government providing special-purpose fu...   
4              F  Active government that is subordinate to anoth...   
5              F  Fictitious entity created to fill the Census B...   
6              G  Active government that is subordinate to anoth...   
7              H  Inactive government providing primary general-...   
8              I  Inactive governmental unit that has the power ...   
9              L  Inactive nonfunctioning legal real property en...   
10             M  Active legal real property entity with quasi-l...   
11             N                        Nonfunctioning legal entity   
12             P  Active government providing special-purpose fu...   
13             S                                 Statistical entity   
14             T                     Active state-recognized entity   

                  fs_short_desc   
0                         Active  
1    Active partial consolidated  
2            Active Consolidated  
3         Active special purpose  
4            Active subordinate   
5                     Fictitious  
6             Active subordinate  
7                       Inactive  
8       Inactive special purpose  
9                       Inactive  
10    Active legal real property  
11          Nonfunctioning legal  
12        Active special purpose  
13                   Statistical  
14       Active state recognized

In [ ]:
pd.set_option('display.max_rows', 500)
#sub_est_df[['SUMLEV', 'sum_lvl_desc', 'NAME', 'use_city']]

#sub_est_df.groupby(['sum_lvl_desc'])['NAME'].count()

#df[df['Value']==df['Value'].max()]

# sub_est_df[sub_est_df['POPESTIMATE2022']==sub_est_df['POPESTIMATE2022'].max()]

#sub_est_df.groupby(['use_city']).count()
#print (len(sub_est_df['use_city'].unique()))
#print (len(sub_est_df['NAME'].unique()))

#sub_est_df[['NAME', 'sum_lvl_desc', 'use_city', 'POPESTIMATE2022']].sort_values(by=['use_city', 'POPESTIMATE2022'] )

#sub_est_df.sort_values(by=['use_city', 'POPESTIMATE2022'] ).duplicated(subset=['use_city'], keep='last')

#sub_est_df.sort_values(by=['use_city', 'POPESTIMATE2022']

#filt = sub_est_df.duplicated(subset=['use_city'], keep="last")
#sub_est_df[filt].sort_values(by=['use_city', 'POPESTIMATE2022'])

#h = sub_est_df.sort_values(by=['use_city', 'POPESTIMATE2022']).duplicated(subset=['use_city'], keep="first")
#sub_est_df[h]

#sub_est_df.sort_values(by=['use_city', 'POPESTIMATE2022'], inplace=True)
#h = sub_est_df.duplicated(subset=['use_city'], keep='first')
#sub_est_df[h].sort_values(by=['use_city', 'POPESTIMATE2022'])

#sub_est_df.groupby('use_city').agg(['POPESTIMATE2022'] = 'max')
#sub_est_df.groupby('use_city').agg()

city_pop = sub_est_df.groupby('use_city')['POPESTIMATE2022'].max() # 1885
print (type(city_pop))





<class 'pandas.core.series.Series'>


In [ ]:
#see_matches = ny_cities_df.merge(city_pop, how='left', left_on='major_city', right_on='use_city')
#display(see_matches)

see_matches['POPESTIMATE2022'].isna().sum() #746


746

In [ ]:
see_matches = ny_cities_df.merge(sub_est_df, how='left', left_on='major_city', right_on='use_city')
#display(see_matches)


major_city  NP_CNT  CNT_NP_RANK    INCOME_AMT  INCOME_RANK  \
0                   New York   20896            0  2.967132e+11            0   
1                   Brooklyn   15084            1  2.284092e+10            2   
2                      Bronx    3971            2  1.628941e+10            3   
3                    Buffalo    3836            3  1.060582e+10            7   
4                  Rochester    2753            4  1.615948e+10            4   
5                     Albany    2163            5  1.534299e+10            5   
6              Staten Island    1680            6  2.059546e+09           14   
7                   Syracuse    1451            7  7.508000e+09            8   
8                   Flushing    1148            8  3.297948e+09           10   
9                    Jamaica    1033            9  2.140089e+09           13   
10                    Monsey    1013           10  6.083412e+08           53   
11                    Ithaca     848           11  1.304681e+10            6   
12               Schenectady     750           12  4.899644e+09            9   
13             Spring Valley     699           13  6.225346e+08           51   
14             Spring Valley     699           13  6.225346e+08           51   
15                   Yonkers     611           14  1.569346e+09           23   
16              White Plains     598           15  1.533774e+09           25   
17                Binghamton     514           16  2.005985e+09           15   
18                  Fairport     501           17  1.059913e+08          180   
19                  Fairport     501           17  1.059913e+08          180   
20                  Fairport     501           17  1.059913e+08          180   
21                    Monroe     496           18  3.516372e+08           80   
22                    Monroe     496           18  3.516372e+08           80   
23                    Monroe     496           18  3.516372e+08           80   
24                    Monroe     496           18  3.516372e+08           80   
25              Poughkeepsie     495           19  3.289074e+09           11   
26                   Astoria     459           20  8.740210e+08           38   
27               Garden City     437           21  1.584398e+09           20   
28               Garden City     437           21  1.584398e+09           20   
29                      Troy     424           22  1.975041e+09           16   
30              New Rochelle     415           23  1.274995e+09           26   
31                Great Neck     380           24  5.111779e+08           59   
32                Great Neck     380           24  5.111779e+08           59   
33                Great Neck     380           24  5.111779e+08           59   
34          Saratoga Springs     377           25  1.180070e+09           27   
35              Mount Vernon     363           26  1.614994e+08          141   
36          Long Island City     354           27  1.576563e+09           21   
37                 Scarsdale     340           28  3.899541e+08           76   
38                 Scarsdale     340           28  3.899541e+08           76   
39                 Scarsdale     340           28  3.899541e+08           76   
40                 Scarsdale     340           28  3.899541e+08           76   
41                  Westbury     326           29  2.289168e+10            1   
42                  Westbury     326           29  2.289168e+10            1   
43                  Westbury     326           29  2.289168e+10            1   
44                  Kingston     323           30  1.133185e+09           29   
45                     Utica     319           31  1.727990e+09           17   
46             New Hyde Park     318           32  8.035468e+08           41   
47             New Hyde Park     318           32  8.035468e+08           41   
48             Valley Stream     316           33  2.585701e+08          102   
49             Val

major_city  NP_CNT  CNT_NP_RANK    INCOME_AMT  INCOME_RANK  \
1                   Brooklyn   15084            1  2.284092e+10            2   
2                      Bronx    3971            2  1.628941e+10            3   
3                    Buffalo    3836            3  1.060582e+10            7   
5                     Albany    2163            5  1.534299e+10            5   
6              Staten Island    1680            6  2.059546e+09           14   
7                   Syracuse    1451            7  7.508000e+09            8   
8                   Flushing    1148            8  3.297948e+09           10   
9                    Jamaica    1033            9  2.140089e+09           13   
10                    Monsey    1013           10  6.083412e+08           53   
12               Schenectady     750           12  4.899644e+09            9   
15                   Yonkers     611           14  1.569346e+09           23   
16              White Plains     598           15  1.533774e+09           25   
26                   Astoria     459           20  8.740210e+08           38   
29                      Troy     424           22  1.975041e+09           16   
30              New Rochelle     415           23  1.274995e+09           26   
34          Saratoga Springs     377           25  1.180070e+09           27   
35              Mount Vernon     363           26  1.614994e+08          141   
36          Long Island City     354           27  1.576563e+09           21   
45                     Utica     319           31  1.727990e+09           17   
51            Queens Village     311           34  1.100832e+08          176   
52        Huntington Station     310           35  5.382067e+07          265   
54              Forest Hills     301           37  3.364869e+08           85   
55              Far Rockaway     294           38  1.549594e+08          147   
62             Niagara Falls     278           43  2.944495e+08           93   
68                 Jamestown     272           46  2.798706e+08           98   
69                  Melville     266           47  4.665825e+08           64   
70           Port Washington     255           48  4.245529e+08           69   
72                  New City     246           50  1.489654e+08          151   
73                  Woodside     246           51  1.650256e+08          140   
75                    Auburn     239           53  5.021379e+08           61   
81              Saint Albans     228           56  9.792432e+07          188   
86             Fresh Meadows     221           58  2.462114e+09           12   
87                   Bayside     215           59  3.079873e+08           90   
88                Hicksville     215           60  1.228424e+08          165   
96                 Bay Shore     210           63  8.256710e+07          204   
97                 Ridgewood     208           64  1.855992e+08          124   
104                   Latham     206           67  1.044004e+09           33   
109                 Elmhurst     204           70  6.968487e+07          233   
110          Jackson Heights     203           71  1.029595e+08          182   
112                  Syosset     202           73  1.226989e+08          166   
113      Springfield Gardens     202           74  4.140313e+07          294   
115                  Jericho     198           76  1.810501e+08          127   
128                Hauppauge     188           81  4.500404e+08           65   
129                     Rome     187           82  2.988706e+08           92   
134               Massapequa     185           85  3.258501e+07          327   
140                Manhasset     184           88  9.945211e+07          187   
141              Glens Falls     181           89  1.303006e+08          160   
146                   Elmont     181           91  1.007748e+08          186   
148               Ronkonkoma     178           93  1.329947e+08          159   
149               

In [ ]:
pd.set_option('display.max_rows', 2600)
display(see_matches)
filt = see_matches['use_city'].isna()
display(see_matches[filt]) #799

In [ ]:
# check out no matches
sub_est_df[sub_est_df['NAME'].str.contains('Saratoga')]



SUMLEV  STATE  COUNTY  PLACE  COUSUB  CONCIT  PRIMGEO_FLAG FUNCSTAT  \
477      162     36       0  65255       0       0             0        A   
2680      50     36      91      0       0       0             0        A   
2686     157     36      91  65255       0       0             0        A   
2692     157     36      91  99990       0       0             0        S   
2722      61     36      91      0   65244       0             0        A   
2725      71     36      91  99990   65244       0             1        F   
2726      61     36      91      0   65255       0             0        F   
2727      71     36      91  65255   65255       0             1        A   

                            NAME    STNAME  ESTIMATESBASE2020  \
477        Saratoga Springs city  New York              28488   
2680             Saratoga County  New York             235499   
2686       Saratoga Springs city  New York              28488   
2692  Balance of Saratoga County  New York             183619   
2722               Saratoga town  New York               5808   
2725    Balance of Saratoga town  New York               3760   
2726       Saratoga Springs city  New York              28488   
2727       Saratoga Springs city  New York              28488   

      POPESTIMATE2020  POPESTIMATE2021  POPESTIMATE2022  \
477             28525            28702            28593   
2680           235794           237962           238797   
2686            28525            28702            28593   
2692           183886           185887           186940   
2722             5817             5860             5864   
2725             3770             3806             3817   
2726            28525            28702            28593   
2727            28525            28702            28593   

                        use_city                                  sum_lvl_desc  
477        Saratoga Springs city                               Place (no CDPs)  
2680             Saratoga County                                        county  
2686       Saratoga Springs city                        Place (no CDPs)-County  
2692  Balance of Saratoga County                        Place (no CDPs)-County  
2722                    Saratoga                             MCD/CCD (10,000+)  
2725         Balance of Saratoga  County Subdivision-Place (10,000+)/Remainder  
2726       Saratoga Springs city                             MCD/CCD (10,000+)  
2727       Saratoga Springs city  County Subdivision-Place (10,000+)/Remainder

### Using cubits sheet

In [ ]:
# NewYork_DemographicsByCity_cubit.csv

fn = proc_dir + "NewYork_DemographicsByCity_cubit.csv"
ny_cubits_df = pd.read_csv(fn)
display(ny_cubits_df)


name       name.1     state  population
0               New York     New York  New York    19571216
1             Adams town        Adams  New York        4910
2          Adams village       Adams   New York        1678
3           Addison town      Addison  New York        2342
4        Addison village     Addison   New York        1564
...                  ...          ...       ...         ...
1521           York town         York  New York        3147
1522      Yorkshire town    Yorkshire  New York        3749
1523       Yorktown town     Yorktown  New York       35268
1524   Yorkville village   Yorkville   New York        2588
1525  Youngstown village  Youngstown   New York        1834

[1526 rows x 4 columns]

In [ ]:
# same prep to match on city name
ny_cubits_df['use_city'] = ny_cubits_df['name'].str.replace(' village', '')
ny_cubits_df['use_city'] = ny_cubits_df['use_city'].str.replace(' town', '')
ny_cubits_df['use_city'] = ny_cubits_df['use_city'].str.replace(' borough', '')
ny_cubits_df['use_city'] = ny_cubits_df['use_city'].str.replace(' city', '')


city_pop = ny_cubits_df.groupby('use_city')['population'].max() # 1283

filt = bmf_cities_p_df['city_population'].isna()
cities_no_pop = bmf_cities_p_df[filt]['major_city'].to_list()
#print(cities_no_pop)
print (len(cities_no_pop))  #429

filt = ny_cubits_df['use_city'].isin(cities_no_pop)
ny_cubits_df[filt]
# ha, this found the same  as usgs



name       name.1     state  population     use_city
141     Bradford town     Bradford  New York         793     Bradford
272  Clarksville town  Clarksville  New York         958  Clarksville
695         Kent town         Kent  New York       12844         Kent

In [ ]:
print (len(city_pop)) # 1283
filt = ny_cubits_df['name'].str.contains('Crittenden')
ny_cubits_df[filt]


Empty DataFrame
Columns: [name, name.1, state, population, use_city]
Index: []

In [ ]:
match_cubits = city_cnty_df.merge(ny_cubits_df, how='left', left_on='major_city', right_on='use_city')
display(match_cubits)

match_cubits['use_city'].isna().sum() #744

print(len(see_matches))




744

In [ ]:
display(ny_cities_df)

major_city  NP_CNT  CNT_NP_RANK    INCOME_AMT  INCOME_RANK
0      New York   20896            0  2.967132e+11            0
1      Brooklyn   15084            1  2.284092e+10            2
2         Bronx    3971            2  1.628941e+10            3
3       Buffalo    3836            3  1.060582e+10            7
4     Rochester    2753            4  1.615948e+10            4
...         ...     ...          ...           ...          ...
1520  Lafayette       1         1520  0.000000e+00         1450
1521      Wayne       1         1521  6.658900e+05          894
1522     Dayton       1         1522  0.000000e+00         1480
1523  Wawarsing       1         1523  0.000000e+00         1500
1524    Howells       1         1524  0.000000e+00         1476

[1525 rows x 5 columns]

### USGS populated places

In [ ]:
# USGS has lists of populated places
# https://prd-tnm.s3.amazonaws.com/StagedProducts/GeographicNames/Topical/PopulatedPlaces_National_Text.zip
# since various census and google commons doens't find
# cities by name, maybe USGS can identify the populated place
# and find the nearest map city.  Also, could use data commons,
# nearby places

# Note: In NYC, there is a city
# Neighborhood Tabulation Area (NTA)*
# for placeslike "Flushing"

# add link to usgs download site
fn = proc_dir + "PopulatedPlaces_National.csv"
usgs_df = pd.read_csv(fn)
display(usgs_df)

# get just new york
filt = usgs_df['state_name'] == 'New York'
usgs_df[filt].shape # (6739, 19)

filt = usgs_df['state_numeric'] == 36
usgs_df[filt]
usgs_df[filt].shape # (6177, 19)


filt = (usgs_df['state_numeric'] == 36) | (usgs_df['state_name'] == 'New York')
usgs_df[filt]
usgs_df[filt].shape # (6739, 19)

filt = (usgs_df['state_numeric'] == 36) | (usgs_df['state_name'] == 'New York')
ny_pop_places = usgs_df[filt]
display(ny_pop_places)
ny_pop_places.to_csv(proc_dir + 'ny_pop_places.csv', index=False)

# what are some cities that aren't found
filt = see_match_df['city_population'].isna()
#see_match_df['major_city'][filt].head(150)
n_city = see_match_df['major_city'][filt].head(150).to_list()
print (n_city)

['Flushing', 'Jamaica', 'Astoria', 'Long Island City', 'Queens Village', 'Forest Hills',
 'Far Rockaway', 'Woodside', 'Saint Albans', 'Fresh Meadows', 'Bayside', 'Ridgewood',
 'Elmhurst', 'Jackson Heights', 'Springfield Gardens', 'Corona', 'Whitestone',
 'East Elmhurst', 'Cambria Heights', 'Delmar', 'Rosedale', 'Richmond Hill', 'Purchase', 'Little Neck',
 'Hollis', 'Ozone Park', 'Rego Park', 'Oakland Gardens', 'South Ozone Park', 'Hastings On Hudson',
 'Getzville', 'College Point', 'West Harrison', 'South Richmond Hill', 'Croton On Hudson', 'Kew Gardens', 'Sunnyside', 'East Amherst', 'Woodhaven', 'Middle Village', 'Saint James', 'Cortlandt Manor', 'Rockaway Park', 'Glenmont', 'Howard Beach', 'Arverne', 'Maspeth', 'Lagrangeville', 'Jamesville', 'Glen Oaks', 'Ballston Lake', 'South Salem', 'Burnt Hills', 'Garnerville', 'Gansevoort', 'Slingerlands', 'Garrison', 'West Henrietta', 'Mohegan Lake', 'Castleton On Hudson', 'North Chili', 'Rexford', 'Lake View', 'Saint Johnsville', 'Poughquag', 'La Fayette', 'Sauquoit', 'Cornwall On Hudson', 'Derby', 'Cross River', 'Stanfordville', 'Tallman', 'Olivebridge', 'East Chatham', 'Greenfield Center', 'Cuddebackville', 'Selkirk', 'Lily Dale', 'Guilderland Center', 'Campbell Hall', 'Slate Hill', 'Palisades', 'Clinton Corners', 'Kirkville', 'Remsenburg', 'Rock Tavern', 'New Hampton', 'Keene Valley', 'Hogansburg', 'Breezy Point', 'De Ruyter', 'Maryknoll', 'Pine City', 'Pine Island', 'Petersburg', 'Glen Spey', 'Saint Regis Falls', 'Pattersonville', 'Bowmansville', 'West Falls', 'Harrisville', 'Craryville', 'East Schodack', 'Mc Graw', 'Sprakers', 'Marietta', 'Ferndale', 'Ray Brook', 'South Wales', 'Ashville', 'Old Chatham', 'Harpursville', 'Branchport', 'Freehold', 'Holmes', 'Harris', 'Cropseyville', 'Waccabuc', 'Blossvale', 'Feura Bush', 'Mumford', 'Goldens Bridge', 'Port Crane', 'East Berne', 'New Woodstock', 'Alfred Station', 'Sidney Center', 'Taberg', 'Howes Cave', 'Porter Corners', 'Boiceville', 'Elizaville', 'Arkville', 'Darien Center', 'Ulster Park', 'Scipio Center', 'Findley Lake', 'Big Indian', 'Varysburg', 'De Kalb Junction', 'Irving', 'Vermontville', 'Croton Falls', 'Diamond Point', 'Ellenburg Depot', 'Bovina Center', 'Saint Bonaventure', 'Spencertown', 'Dewittville', 'Putnam Station']


filt = ny_pop_places['feature_name'].str.contains('Forest Hills')
ny_pop_places[filt]
# just gets map name Jamaica, which is also not found
# the lat lng could be used to reverse geocode to some kind of place with pop

filt = ny_pop_places['feature_name'].str.contains('Elmhurst')
ny_pop_places[filt]

filt = ny_pop_places['feature_name'].str.contains('Getzville')
ny_pop_places[filt]
# map name: Tonawanda East
# wikipedia: Getzville is a hamlet in the town of Amherst in Erie County, New York,

filt = ny_pop_places['feature_name'].str.contains('Stow'))
ny_pop_places[filt]

filt = (usgs_df['feature_name'].str.contains('Crittenden')) & (usgs_df['state_numeric'] == 36)
usgs_df[filt]

filt = usgs_df['feature_name'].isin(cities_no_pop) & (usgs_df['state_numeric'] == 36)
usgs_df[filt]

filt = bmf_cities_p_df['major_city'] == 'Apulia Station'
bmf_cities_p_df[filt]
# has map name Tully

filt = cnty_sub_df['county_sub_name'] == 'Tully'
cnty_sub_df[filt]

check_city = 'Acra'

filt = (usgs_df['feature_name'] == check_city) & (usgs_df['state_numeric'] == 36)
usgs_df[filt]

filt = bmf_cities_p_df['major_city'] == check_city
bmf_cities_p_df[filt]
# has map name Freehold

filt = cnty_sub_df['county_sub_name']  == 'Freehold'
cnty_sub_df[filt]

filt = acs5_place_df['use_city'] ==  'Freehold'
acs5_place_df[filt]

# wikipedia: Acra is a hamlet in Greene County, New York, United States.




feature_id feature_name    feature_class state_name state_numeric  \
77585      951053    Getzville  Populated Place   New York            36   

      county_name county_numeric        map_name date_created date_edited  \
77585        Erie             29  Tonawanda East   01/23/1980  02/13/2020   

      bgn_type bgn_authority bgn_date prim_lat_dms prim_long_dms prim_lat_dec  \
77585      NaN           NaN      NaN      430126N      0784604W    43.023947   

      prim_long_dec  Unnamed: 17  Unnamed: 18  
77585    -78.767811          NaN          NaN

# Misc

In [ ]:
# Unsused
#chat gpt places, census designated places

import requests
import pandas as pd

# Replace this with your own Census API key
API_KEY = 'your_census_api_key_here'

# Set the state FIPS code for New York (36)
STATE_CODE = "36"

# Base URL for the Census API - using the 2020 Decennial Census endpoint
base_url = "https://api.census.gov/data/2020/dec/pl"

# Function to get all places in New York State
def get_places(state_code=STATE_CODE):
    # Set parameters for the API request
    params = {
        'get': 'NAME',
        'for': 'place:*',
        'in': f'state:{state_code}',
        'key': API_KEY
    }

    # Make the API request
    response = requests.get(base_url, params=params)

    # Check if the request was successful
    if response.status_code == 200:
        data = response.json()
        # Convert to pandas DataFrame
        columns = ['Place_Name', 'state', 'place']
        places_data = pd.DataFrame(data[1:], columns=columns)
        return places_data
    else:
        print(f"Error: Unable to fetch data. Status code {response.status_code}")
        return None

# Fetch places data for New York
places_data = get_places()

# If data is fetched successfully, save it to a CSV
if places_data is not None:
    # Drop the 'state' column as it's not needed for display
    places_data.drop(columns=['state'], inplace=True)
    # Save the data to a CSV file
    places_data.to_csv('ny_places.csv', index=False)
    print("Data saved to ny_places.csv")
else:
    print("Failed to retrieve places data.")



In [ ]:
# sum of income by city

df.groupby(['CITY'])['INCOME_AMT'].sum().nlargest(10)

#df.groupby(['CITY'])['INCOME_AMT'].sum().nlargest(10).plot()



CITY
NEW YORK     2.963530e+11
WESTBURY     2.289168e+10
BROOKLYN     2.281771e+10
ROCHESTER    1.615927e+10
BRONX        1.595391e+10
ALBANY       1.328867e+10
ITHACA       1.304678e+10
BUFFALO      8.772831e+09
SYRACUSE     7.100577e+09
FLUSHING     5.700128e+09
Name: INCOME_AMT, dtype: float64

In [ ]:
# ----- obselete -------------
# Orgs and IRS Income Code
# This version only does lookup for columns where there is data

#result = df.groupby(['INCOME_CD'])['p_org_id'].count().sort_values(ascending=False)

result = df.groupby(['INCOME_CD'])['p_org_id'].count()
print (result.index)

for x in result.index:
  x = str(x)
  print (bmf['INCOME_CD'][x]['short'])
  xlabs.append(f"({x})  {bmf['INCOME_CD'][x]['short']} ")


#for c in (c for c in bmf['INCOME_CD'] if c != 'define') :
#  print (c, ":", bmf['INCOME_CD'][c]['full'

#display(result)

#print (type(result))
#print (result[0], result[1])
#print (result.values)
#print (result.index.sort)


Index([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], dtype='int64', name='INCOME_CD')


NameError: name 'bmf' is not defined

In [ ]:
# ranking cities by income?
# ideally plotting rank ranges

#result =
#print (df.groupby(['CITY'])['INCOME_AMT'].sum().rank().sort_values())
#df.groupby("group_ID")["value"].rank(method="dense", ascending=False)

# df.groupby("CITY")["INCOME_AMT"].rank(method="dense", ascending=False)

# df.sort_values(by=['group_ID', 'value']).groupby('group_ID').cumcount(ascending=False) + 1

# df.groupby("CITY")["INCOME_AMT"].sum().sort_values(ascending=False) #.cumcount(ascending=False) + 1

#df['rank'] = df.sort_values(by=['group_ID', 'value']).groupby('group_ID').cumcount(ascending=False) + 1

#for method in ['average', 'min', 'max', 'dense', 'first']:
#    df[f'{method}_rank'] = df.groupby('group')['value'].rank(method)

#for method in ['average', 'min', 'max', 'dense', 'first']:
  # df[f'{method}_rank'] = df.groupby('CITY')['INCOME_AMT'].rank(method)
#  print (df.groupby('CITY')['INCOME_AMT'].rank(method))

#df.groupby('CITY')['INCOME_AMT'].sum().rank()

#city_inc_df = df.groupby("CITY")["INCOME_AMT"].sum().sort_values(ascending=False)

#g1 = df1.groupby(["Name", "City"], as_index=False).count()


# this looks to get cities by sum of income ordered by index
# the reset index creates both columns..
city_inc_df = df.groupby("CITY")["INCOME_AMT"].sum().sort_values(ascending=False).reset_index()

#city_inc_df["rank"] = city_inc_df.groupby("CITY")["INCOME_AMT"].rank(method="dense", ascending=False)
# display(city_inc_df)

#for method in ['average', 'min', 'max', 'dense', 'first']:
  # df[f'{method}_rank'] = df.groupby('CITY')['INCOME_AMT'].rank(method)





In [ ]:

d = get_census( info['county_fips'],
        info['state_fips'],
        'timeseries',
        'poverty',
        'saipe',
        '2018',
        cols)


# -- the yr parameter only used sometimes
def get_census (county, state, year, dsource, dname, yr, cols):

    base_url = f'https://api.census.gov/data/{year}/{dsource}/{dname}'

    if yr == 'na':
        data_url = f'{base_url}?get={cols}&for=county:{county}&in=state:{state}&key={api_key}'
    else:
        data_url = f'{base_url}?get={cols}&for=county:{county}&in=state:{state}&time={yr}&key={api_key}'

    response=requests.get(data_url)




In [ ]:
# wah = city_inc_df.iloc[10:20]


filt = city_inc_df['CITY'].isin(['CORTLAND', 'AUBURN', 'ELMIRA', 'HOMER'])
city_inc_df[filt]

#wah = city_inc_df[filt]

# ok ranked citys

rank_start = 0
rank_end = 24

wah = city_inc_df.iloc[rank_start:rank_end]

#city_inc_df.iloc[10:20]

xlabs = wah['CITY']
#print (xlabs)
inc = wah['INCOME_AMT']
#print (inc)

label_format = '{:,.0f} M'

fig, ax1 = plt.subplots()
#fig, (ax1, ax2)  = plt.subplots(2, 1)

#TODO: horizontal bar, switch x and y
ax1.bar(#result.index,
        xlabs,
        #result.values,
        inc / 1000000,
        #color='#FF0000',
        label='Sum of Orgs Income')
ax1.legend()
#ax1.set_xticklabels(result.index, rotation=90)

# avoid weird warning...
#ax1.xaxis.set_ticks(result.index)
#ax1.xaxis.set_ticklabels(result.index,rotation=90)

#ax1.xaxis.set_ticks(city_inc_df[filt].index)
ax1.xaxis.set_ticklabels(wah['CITY'],rotation=90)



# this odd line remove warning to use formatter before locator
ax1.set_yticks(ax1.get_yticks())
ticks_loc = ax1.get_yticks().tolist()
ax1.set_yticklabels([label_format.format(x) for x in ticks_loc])


ax1.set_xlabel('NTEE Category')
ax1.set_ylabel('Orgs Income')
ax1.set_title(f"Cites NP Income: Ranked {rank_start + 1} to {rank_end + 1} ")

plt.show()



In [ ]:
# plotting selected cities and Income Sum
# result = cortland_df.groupby(['ntee_cat'])['INCOME_AMT'].sum().sort_values(ascending=False)

filt = df['CITY'].isin(['CORTLAND', 'AUBURN', 'ELMIRA', 'HOMER'])

#result = df.groupby(['CITY'])['INCOME_AMT'].sum().nlargest(10)
result = df[filt].groupby(['CITY'])['INCOME_AMT'].sum().nlargest(10)

label_format = '{:,.0f} M'

fig, ax1 = plt.subplots()
#fig, (ax1, ax2)  = plt.subplots(2, 1)

ax1.bar(result.index,
        #result.values,
        result.values / 1000000,
        #color='#FF0000',
        label='Sum of Orgs Income')
ax1.legend()
#ax1.set_xticklabels(result.index, rotation=90)

# avoid weird warning...
ax1.xaxis.set_ticks(result.index)
ax1.xaxis.set_ticklabels(result.index,rotation=90)

# this odd line remove warning to use formatter before locator
ax1.set_yticks(ax1.get_yticks())
ticks_loc = ax1.get_yticks().tolist()
ax1.set_yticklabels([label_format.format(x) for x in ticks_loc])


ax1.set_xlabel('City')
ax1.set_ylabel('Orgs Income')
ax1.set_title('NY NP Orgs Income by City')

plt.show()


In [ ]:
filt = city_inc_df['CITY'].isin(['CORTLAND', 'AUBURN', 'ELMIRA', 'HOMER'])
city_inc_df[filt]

In [ ]:
#
#city_inc_df.info()

#city_inc_df.index(start=1, stop=10)
#city_inc_df.item()

#city_inc_df.filter(items=[5,8], axis=0)
#print (type(city_inc_df))
#city_inc_df.info()

# city_inc_df.filter(items=range(10, 20), axis=0)
# result = cortland_df.groupby(['ntee_cat'])['INCOME_AMT'].sum().sort_values(ascending=False)

result = city_inc_df.filter(items=range(10, 20), axis=0)

print (result.index[0], result.values[1][0])


In [ ]:
# swap x y


# wah = city_inc_df.iloc[10:20]
#filt = city_inc_df['CITY'].isin(['CORTLAND', 'AUBURN', 'ELMIRA', 'HOMER'])
#city_inc_df[filt]

#wah = city_inc_df[filt]

# ok ranked cities

rank_start = 0
rank_end = 24

wah = city_inc_df.iloc[rank_start:rank_end]

yax = wah['CITY']
yax_pos = np.arange(len(yax))


#city_inc_df.iloc[10:20]
# xlabs = wah['CITY']
# inc = wah['INCOME_AMT']
xax = wah['INCOME_AMT']


#print (xax)
#print (yax)

label_format = '{:,.0f} M'

fig, ax1 = plt.subplots()
#fig, (ax1, ax2)  = plt.subplots(2, 1)

#TODO: horizontal bar, switch x and y
ax1.barh(yax_pos, #xax,
         wah['INCOME_AMT'], # yax,
        #wah['INCOME_AMT'],
        #color='#FF0000',
        label='Sum of Orgs Income')
ax1.legend()
#ax1.set_xticklabels(result.index, rotation=90)

# avoid weird warning...
#ax1.xaxis.set_ticks(result.index)


#ax1.xaxis.set_ticks(wah.index)
#ax1.xaxis.set_ticklabels(wah.index,rotation=90)

ax1.xaxis.set_ticks(xax.index)
ax1.xaxis.set_ticklabels(xax,rotation=90)


#ax1.xaxis.set_ticks(city_inc_df[filt].index)
#ax1.yaxis.set_ticklabels(wah['CITY'])
ax1.yaxis.set_ticklabels(yax)

# this odd line remove warning to use formatter before locator
#ax1.set_xticks(ax1.get_xticks())
ticks_loc = ax1.get_xticks().tolist()
ax1.set_xticklabels([label_format.format(x) for x in ticks_loc])


#ax1.set_xlabel('NTEE Category')
#ax1.set_ylabel('Orgs Income')
#ax1.set_title(f"Cites NP Income: Ranked {rank_start + 1} to {rank_end + 1} ")

plt.show()






In [ ]:

df[['INCOME_AMT', 'REVENUE_AMT']].sum()

In [ ]:
# miscellanous lookups and tests

# just prints the column
# cortland_df['NTEE_CD']

# cortland_df['NTEE_CD', 'INCOME_AMT'].groupby(['NTEE_CD']).sum("INCOME_AMT")

# works
#df_tmp =  cortland_df.groupby(['NTEE_CD'])['INCOME_AMT'].describe()
#display(df_tmp)
#del df_tmp

# cortland_df.T.describe()

# key error
# cortland_df.T['INCOME_AMT'].describe()

# works
#cortland_df['INCOME_AMT'].describe()

# cortland_df['INCOME_AMT'].sum()

# cortland_df.groupby(['NTEE_CD'])['INCOME_AMT'].sum()

# works
# cortland_df.agg({'INCOME_AMT' : ['sum', 'min', 'max', 'mean', 'std']})

# df.groupby(['team', 'position'])['points', 'rebounds'].sum().reset_index()
# cortland_df.groupby(['NTEE_CODE'])['INCOME_AMT'].sum().reset_index()

#cortland_df.agg({'INCOME_AMT' : ['sum', 'min']}, axis="columns")

#np.std(cortland_df['INCOME_AMT'])

# np.median(cortland_df['INCOME_AMT'])
# np.average(cortland_df['INCOME_AMT'])



In [ ]:
# putting income into bins

bins = [0,1,10000,50000,100000,200000, 500000,1000000, 2000000]

# works, but seems to leave off nulls(?). labels clearly by bin
#cortland_df['NAME'].groupby(pd.cut(cortland_df['INCOME_AMT'], bins)).count()

# works: (-0.001, 1.0]
cortland_df['INCOME_AMT'].value_counts(bins=bins, sort=False)


In [ ]:

# cortland_df.groupby(['NTEE_CD'])['INCOME_AMT'].describe()[['count', 'mean']]  # no error

# cortland_df.groupby(['CITY'])['INCOME_AMT'].describe()[['count', 'mean']]  # no error


# not fiddled
# df.describe(percentiles=[.10, .20, .30, .40, .50, .60, .70, .80, .90]))



In [ ]:
# cortland_df.groupby(['NTEE_CD'][0])['EIN'].agg('count') # gives a df that counts values
#df.groupby('a').apply(lambda x: x['b'].sum()/x['c'].sum()) # stack exchange

# cortland_df.groupby(['NTEE_CD']).apply(lambda x: x['INCOME_AMT'].sum())

# se
# even_odd = ['even' if i%2==0 else 'odd' for i in df['A']]
# df.groupby(even_odd)['B'].mean()

#cortland_df.info()

# ntee_cat = [  "yes" if i else 'nan' for i in cortland_df['NTEE_CD']]
# cortland_df['ntee_cat'].value_counts()

# --- works ---
# ntee_cat = [  str(i)[0] if i else 'nan' for i in cortland_df['NTEE_CD']]
# cortland_df.groupby(ntee_cat)['INCOME_AMT'].sum().reset_index()

# --- fiddle ---
ntee_cat = [  str(i)[0] if i else 'nan' for i in cortland_df['NTEE_CD']]
#cortland_df.groupby(ntee_cat)['INCOME_AMT'].sum()
tmp = cortland_df.groupby(ntee_cat)['INCOME_AMT'].sum()

#tmp.plot(legend=True)
tmp.plot.bar(legend=True)


In [ ]:
# --- get census data for cities ---
# Not done, saving as fodder for later

import requests
import ast

from google.colab import userdata
ckey = userdata.get('census_api_key')

#https://stackoverflow.com/questions/28933220/us-census-api-get-the-population-of-every-city-in-a-state-using-python

#base_url = 'http://api.census.gov/data/%s/%s?key=%s&get=' % (str(year), dataset, self.key)

url = f'http://api.census.gov/data/2020/sf1?key={ckey}&get=P0010001&in=state:36'

print (url)


'''
county = c.get(['P0010001'], ['in=state:25', 'for=county:*'])
# url: http://api.census.gov/data/2010/sf1?key=<mykey>&get=P0010001&in=state:25&for=county:*

city = c.get(['P0010001'], ['in=state:25', 'for=place:*'])
# url: http://api.census.gov/data/2010/sf1?key=<mykey>&get=P0010001&in=state:25&for=place:*


def get_stuff(fields, geo, year=2010, dataset='sf1'):
    fields = [','.join(fields)]
    base_url = 'http://api.census.gov/data/%s/%s?key=%s&get=' % (str(year), dataset, self.key)
    query = fields
    for item in geo:
        query.append(item)
    add_url = '&'.join(query)
    url = base_url + add_url
    print(url)
    req = urllib.request.Request(url)
    response = urllib.request.urlopen(req)
    return response.read()

c = Census('<mykey>')
state = c.get(['P0010001'], ['for=state:25'])
# url: http://api.census.gov/data/2010/sf1?key=<mykey>&get=P0010001&for=state:25
county = c.get(['P0010001'], ['in=state:25', 'for=county:*'])
# url: http://api.census.gov/data/2010/sf1?key=<mykey>&get=P0010001&in=state:25&for=county:*
city = c.get(['P0010001'], ['in=state:25', 'for=place:*'])
# url: http://api.census.gov/data/2010/sf1?key=<mykey>&get=P0010001&in=state:25&for=place:*

# Cast result to list type
state_result = ast.literal_eval(state.decode('utf8'))
county_result = ast.literal_eval(county.decode('utf8'))
city_result = ast.literal_eval(city.decode('utf8'))

def count_pop_county():
    count = 0
    for item in county_result[1:]:
        count += int(item[0])
    return count

def count_pop_city():
    count = 0
    for item in city_result[1:]:
        count += int(item[0])
    return count

'''





In [ ]:
# i think this might turn into text which can't be summed
df['INCOME_AMT'] = df['INCOME_AMT'].apply('${:,.0f}'.format)
df['REVENUE_AMT'] = df['REVENUE_AMT'].apply('${:,.0f}'.format)
df['ASSET_AMT'] = df['ASSET_AMT'].apply('${:,.0f}'.format)



In [ ]:
# reference
# looks like default behavior is adding plot will add plots
# seeming without subplot, fig, or ax

# creating dataframe
df_t = pd.DataFrame({
    'X': [1, 2, 3, 4, 5],
    'Y': [2, 4, 6, 10, 15]
})

# plotting a line graph
print("Line graph: ")
plt.plot(df_t["X"], df_t["Y"])
plt.show()

# plotting a scatter plot
print("Scatter Plot:  ")
plt.scatter(df_t["X"], df_t["Y"])
plt.show()
